In [1]:
pip list

Package                      Version             
---------------------------- --------------------
absl-py                      0.15.0              
alembic                      1.7.5               
apturl                       0.5.2               
argon2-cffi                  21.3.0              
argon2-cffi-bindings         21.2.0              
asttokens                    2.0.5               
astunparse                   1.6.3               
atomicwrites                 1.1.5               
attrs                        19.3.0              
autopage                     0.4.0               
backcall                     0.2.0               
bcrypt                       3.1.7               
beautifulsoup4               4.8.2               
black                        21.12b0             
bleach                       4.1.0               
blinker                      1.4                 
Brlapi                       0.7.0               
cachetools                   4.2.4               


Note: you may need to restart the kernel to use updated packages.


In [2]:
import numpy as np
import matplotlib.pyplot as plt
from sklearn import preprocessing
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_absolute_percentage_error
from keras.models import Sequential
from keras.layers import Dense, SimpleRNN, Input, Activation, Dropout
from keras import backend as K
from tensorflow.keras.optimizers import Adam,SGD
import tensorflow as tf
from keras.models import Model
import copy



In [3]:
#disable the GPU

try:
    # Disable all GPUS
    tf.config.set_visible_devices([], 'GPU')
    visible_devices = tf.config.get_visible_devices()
    for device in visible_devices:
        assert device.device_type != 'GPU'
except:
    # Invalid device or cannot modify virtual devices once initialized.
    pass

2023-09-08 10:26:09.707370: I tensorflow/stream_executor/cuda/cuda_gpu_executor.cc:936] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero
2023-09-08 10:26:09.727467: I tensorflow/stream_executor/cuda/cuda_gpu_executor.cc:936] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero
2023-09-08 10:26:09.727607: I tensorflow/stream_executor/cuda/cuda_gpu_executor.cc:936] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero


In [4]:
# specifying constant parameters

T_0 = 300.0
V = 1.0
k_0 = 8.46*(np.power(10,6))
C_p = 0.231
rho_L = 1000.0
Q_s = 0.0
T_s = 402.0
F = 5.0
E = 5.0*(np.power(10,4))
delta_H = -1.15*(np.power(10,4))
R = 8.314
C_A0s = 4.0
C_As = 1.95
t_final = 0.01
t_step = 1e-4
P = np.array([[1060.0, 22.0], [22.0, 0.52]])


In [5]:
# generating inputs and initial states for CSTR, all expressed in deviation form

u1_list = np.linspace(-3.5, 3.5, 5, endpoint=True)
u2_list = np.linspace(-5e5 * 1.0, 5e5 * 1.0, 5, endpoint=True)
T_initial = np.linspace(300.0, 600.0, 80, endpoint=True) - T_s
CA_initial = np.linspace(0.0, 6.0, 80, endpoint=True) - C_As


In [6]:
# sieve out initial states that lie outside of stability region

T_start = list()
CA_start = list()

for T in T_initial:
    for CA in CA_initial:
        x = np.array([CA, T])
        if x @ P @ x < 372:
            CA_start.append(CA)
            T_start.append(T)
print("number of initial conditions: {}".format(len(CA_start)))

# convert to np.arrays
CA_start = np.array([CA_start])
T_start = np.array([T_start])
x_deviation = np.concatenate((CA_start.T, T_start.T), axis=1)  # every row is a pair of initial states within stability region
print("shape of x_deviation is {}".format(x_deviation.shape))

number of initial conditions: 500
shape of x_deviation is (500, 2)


In [7]:
def CSTR_simulation_derivative( C_A_initial, T_initial, C_A0, Q):
    
    C_A = C_A_initial + C_As
    T = T_initial + T_s
    
    dCAdt = F / V * (C_A0 - C_A) - k_0 * np.exp(-E / (R * T)) * C_A**2
    dTdt = F / V * (T_0 - T) -  delta_H / (rho_L * C_p) * k_0 * np.exp(-E / (R * T)) * C_A**2 + Q / (rho_L * C_p * V)
    
    return dCAdt, dTdt

In [8]:
# get X and y data for training and testing

dCAdt_output = list()
dTdt_output = list()
CA_input = list()
T_input = list()
CA0_input = list()
Q_input = list()

for u1 in u1_list:
    C_A0 = u1 + C_A0s
    
    for u2 in u2_list:
        Q = u2 + Q_s
        
        for C_A_initial, T_initial in x_deviation:
            CA0_input.append(u1)
            Q_input.append(u2)
            CA_input.append(C_A_initial)
            T_input.append(T_initial)
            
            dCAdt, dTdt = CSTR_simulation_derivative( C_A_initial, T_initial, C_A0, Q)
            dCAdt_output.append([dCAdt])
            dTdt_output.append([dTdt])


In [9]:
# collate input for RNN

CA0_input = np.array(CA0_input)
CA0_input = CA0_input.reshape(-1,1)
print("CA0_input shape is {}".format(CA0_input.shape))

Q_input = np.array(Q_input)
Q_input = Q_input.reshape(-1,1)
print("q_input shape is {}".format(Q_input.shape))

CA_input = np.array(CA_input)
CA_input = CA_input.reshape(-1,1)
print("CA_input shape is {}".format(CA_input.shape))

T_input = np.array(T_input)
T_input = T_input.reshape(-1,1)
print("T_input shape is {}".format(T_input.shape))

NN_input = np.concatenate(( CA_input, T_input, CA0_input, Q_input), axis=1)
print("NN_input shape is {}".format(NN_input.shape))



CA0_input shape is (12500, 1)
q_input shape is (12500, 1)
CA_input shape is (12500, 1)
T_input shape is (12500, 1)
NN_input shape is (12500, 4)


In [10]:

print(NN_input[0, 0])
print(NN_input[0, 1])

1.4677215189873418
-75.41772151898732


In [11]:
# collate output for RNN

dCAdt_output = np.array(dCAdt_output)
dCAdt_output = dCAdt_output.reshape(-1,1)

dTdt_output = np.array(dTdt_output)
dTdt_output = dTdt_output.reshape(-1, 1)

NN_output = np.concatenate((dCAdt_output, dTdt_output), axis=1)
print("RNN_output shape is {}".format(NN_output.shape))  # output shape: number of samples x timestep x variables

RNN_output shape is (12500, 2)


In [12]:
import copy
# split into train and test sets
X_train, X_test, y_train, y_test = train_test_split(NN_input, NN_output, test_size=0.3, random_state=123)

X_train_copy = tf.constant(copy.deepcopy(X_train), dtype = tf.float32)
X_test_copy = tf.constant(copy.deepcopy(X_test), dtype = tf.float32)
X_all_copy = tf.constant(copy.deepcopy(NN_input), dtype = tf.float32)


# define scalers for both X and y base on training data only
scaler_X = preprocessing.StandardScaler(with_mean = False).fit(X_train)
scaler_y = preprocessing.StandardScaler(with_mean = False).fit(y_train)

print(scaler_X.mean_)
print(scaler_y.mean_)
print(scaler_X.scale_)
print(scaler_y.scale_)

# These are basically tf (tensorflow) matrices to convert the x and u from the original form into normalized form and convert y from normalized
# form to original form. So D_x x is the normalized version of x, and D_u u is the normalized version of u, and D_y (output) is the original form of y.

D_x = tf.constant([[1/scaler_X.scale_[0],0],[0,1/scaler_X.scale_[1]]],dtype = tf.float32)
D_u = tf.constant([[1/scaler_X.scale_[2],0],[0,1/scaler_X.scale_[3]]],dtype = tf.float32)
D_y = tf.constant([[scaler_y.scale_[0],0],[0,scaler_y.scale_[1]]], dtype = tf.float32)

print(D_u)
print(D_y)

X_train = scaler_X.transform(X_train)
X_test = scaler_X.transform(X_test)
y_train = scaler_y.transform(y_train)
y_test = scaler_y.transform(y_test)

[ 9.87558770e-03 -3.23761302e-01  8.00000000e-03  1.17142857e+03]
[  1.33820414 -60.11610829]
[8.48111755e-01 3.83758131e+01 2.47641596e+00 3.53440315e+05]
[  13.73299569 1548.55957516]
tf.Tensor(
[[4.0380937e-01 0.0000000e+00]
 [0.0000000e+00 2.8293321e-06]], shape=(2, 2), dtype=float32)
tf.Tensor(
[[  13.732996    0.      ]
 [   0.       1548.5596  ]], shape=(2, 2), dtype=float32)


2023-09-08 10:26:12.439622: I tensorflow/core/platform/cpu_feature_guard.cc:151] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  AVX2 AVX512F FMA
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.


In [13]:
# checking X_train
print(X_train[0, 0])
print(X_train[0, 1])

1.820126741718589
-1.8662862721343012


In [ ]:
Develop

In [14]:

# This function outputs the value of sontag controller  u interms of a (LfV) and b (LgV). I used a and b this way throughout the rest of the code. 
# Remember that in the sontag law we only use 1 controlled
# variable, which is the heat input Q. 



def phi(a,b):
    factor = - (a + np.sqrt(a**2 + b**4)) / (b**2)
    psi  =  factor * b
    if psi > 500000:
        psi = 500000
    if psi < -500000:
        psi = -500000
    #print(a,b,psi)
    return psi 

def phi_2(a,b):  ###get CA0
    factor = - (a + np.sqrt(a**2 + b**4)) / (b**2)
    psi  =  factor * b
    if psi > 3.5:
        psi = 3.5
    if psi < -3.5:
        psi = -3.5
    #print(a,b,psi)
    return psi 

In [15]:
def CSTR_simulation_derivative2( C_A_initial, T_initial, C_A0, Q):
    
    C_A = C_A_initial + C_As
    T = T_initial + T_s
    
    dCAdt = F / V * (C_A0 - C_A) - k_0 * np.exp(-E / (R * T)) * C_A**2
    dTdt = F / V * (T_0 - T) -  delta_H / (rho_L * C_p) * k_0 * np.exp(-E / (R * T)) * C_A**2 + Q / (rho_L * C_p * V)
    
    return tf.constant(np.array([dCAdt, dTdt]), shape = (2,1))


### this function checks if V is leq 5, and if so, just return a very large negative value. The reason is because this very large negative value 
### will output 0 when passed into the ReLU function.

def modified_dVdt(C_A, T, dVdt):
    x = np.array([C_A,T])
    V = x @ P @ x
    if V <= 12:
        return -1e5
    else:
        return dVdt

### this is f for the FP model in Eq. 1
def f_fp(C_A, T):
    C_A = C_A + C_As
    T = T + T_s

    f1 = F / V * (- C_A) - k_0 * np.exp(-E / (R * T)) * C_A**2
    f2 = F / V * (T_0 - T) - delta_H / (rho_L * C_p) * k_0 * np.exp(-E / (R * T)) * C_A**2 
    f1s = F / V * (- C_As) - k_0 * np.exp(-E / (R * T_s)) * C_As** 2
    f2s = F / V * (T_0 - T_s) - delta_H / (rho_L * C_p) * k_0 * np.exp(-E / (R * T_s)) * C_As**2
    
    return tf.constant(np.array([f1-f1s, f2-f2s]), shape = (2,1))

### this is g for the FP model in Eq. 1
def g_fp():
    return tf.constant(np.array([[F / V , 0],[0, 1/ (rho_L * C_p * V)]]) , shape = (2,2), dtype = tf.float32)

### this is dVdt using Sontag controller without taking into account states that are below \rho_s
def dVsontag_fp(curr_states):
    input_tensor = tf.reshape(curr_states, (curr_states.shape[0] , 1 , 2))
    two_times_x_times_P = tf.stack([ 2 * elem @ tf.convert_to_tensor(P, dtype = tf.float32) for elem in tf.unstack(input_tensor)]) 
    f = tf.map_fn( lambda x : f_fp(x[0,0],x[0,1]) , input_tensor)
    LfV = tf.matmul(two_times_x_times_P, f)
    a = LfV
    g = tf.stack([g_fp() for elem in tf.unstack(input_tensor)])
    dVdx_times_g = tf.matmul(two_times_x_times_P , g)
    b =  tf.gather(dVdx_times_g, [1], axis = 2)
    a_b = tf.concat([a,b],axis = 2)
    ab = tf.reshape(a_b, (curr_states.shape[0], 2))
    sontags = tf.reshape(tf.map_fn(lambda elem : phi(elem[0],elem[1]) , ab ), (curr_states.shape[0],1,1))
    LgVu = tf.matmul(b,sontags)
    dVdt = tf.reshape(a + LgVu,(curr_states.shape[0],1))
    return dVdt 

### this is dVdt using Sontag controller taking into account states that are below \rho_s
def dVsontag_fp_modified(curr_states):
    dVdt = dVsontag_fp(curr_states)
    new_input = tf.concat([input_tensor, dVdt], axis = 2)
    inputs2 = tf.reshape(new_input , (curr_states.shape[0],3))
    return tf.map_fn(lambda elem : modified_dVdt(elem[0],elem[1],elem[2]) , inputs2)


### this is Sontag controller without taking into account states that are below \rho_s
def dVsontag_fp_sontag(curr_states):
    input_tensor = tf.reshape(curr_states, (curr_states.shape[0] , 1 , 2))
    two_times_x_times_P = tf.stack([ 2 * elem @ tf.convert_to_tensor(P, dtype = tf.float32) for elem in tf.unstack(input_tensor)]) 
    f = tf.map_fn( lambda x : f_fp(x[0,0],x[0,1]) , input_tensor)
    LfV = tf.matmul(two_times_x_times_P, f)
    a = LfV
    g = tf.stack([g_fp() for elem in tf.unstack(input_tensor)])
    dVdx_times_g = tf.matmul(two_times_x_times_P , g)
    b =  tf.gather(dVdx_times_g, [1], axis = 2)
    a_b = tf.concat([a,b],axis = 2)
    ab = tf.reshape(a_b, (curr_states.shape[0], 2))
    sontags = tf.reshape(tf.map_fn(lambda elem : phi(elem[0],elem[1]) , ab ), (curr_states.shape[0],1,1))
    
    return sontags


### this is Sontag controller taking into account states that are below \rho_s
def dVsontag_fp_modified_sontag(curr_states):
    input_tensor = tf.reshape(curr_states, (curr_states.shape[0] , 1 , 2))
    dVdt = dVsontag_fp(curr_states)
    new_input = tf.concat([input_tensor, dVdt], axis = 2)
    inputs2 = tf.reshape(new_input , (curr_states.shape[0],3))
    return inputs2



class ControlAffineNN(tf.keras.Model):

    def __init__(self, state_dim, control_dim, f_layers_list, g_layers_list):
        super(ControlAffineNN, self).__init__()
        self.control_dim = control_dim
        self.state_dim = state_dim
        self.f_layers_list = f_layers_list
        self.g_layers_list = g_layers_list

        self.f_layers = []
        for i in range(len(f_layers_list)):
            self.f_layers.append(Dense(f_layers_list[i], activation = 'relu'))
        self.f_layers.append(Dense(state_dim, activation = 'linear'))

        self.g_layers = []
        for i in range(len(g_layers_list)):
            self.g_layers.append(Dense(g_layers_list[i], activation = 'relu'))
        self.g_layers.append(Dense(state_dim * control_dim, activation = 'linear'))
    
    def call(self, inputs):
        print(inputs.shape[0])
        state = inputs[:,0:self.state_dim]
        control = tf.reshape(inputs[:,self.state_dim::], (inputs.shape[0], self.control_dim , 1 ))

        f = tf.identity(state)
        for layer in self.f_layers:
            f = layer(f)

        g = tf.identity(state)
        for layer in self.g_layers:
            g = layer(g)      
        g = tf.reshape( g, (inputs.shape[0], self.state_dim , self.control_dim ) )


        gu = tf.reshape(tf.matmul(g,control) , (inputs.shape[0], self.state_dim))
    
        return f + gu
    
    def get_config(self):
        config = super(ControlAffineNN, self).get_config()
        config['state_dim'] = self.state_dim
        config['control_dim'] = self.control_dim
        config['f_layers_list'] = self.f_layers_list
        config['g_layers_list'] = self.g_layers_list
        return config

### this is f for the NN model
    def f_nn(self,curr_states):
        f = tf.identity(curr_states)
        for layer in self.f_layers:
            f = layer(f)
        return f

### this is g for the NN model

    def g_nn(self,curr_states):
        g = tf.identity(curr_states)
        for layer in self.g_layers:
            g = layer(g)      
        g = tf.reshape( g, (curr_states.shape[0], self.state_dim , self.control_dim ) )
        return g

### this is F_nn for the NN model

    def dxdt(self,curr_states_unnormalized):
        curr_states = tf.constant(scaler_X.transform(curr_states_unnormalized),dtype = tf.float32)
        dxdt_normalized = self.call(curr_states)
        return scaler_y.inverse_transform(dxdt_normalized)


### this is dVdt for the NN model [\nabla V F_nn (x, sontag(x))]
### this is where the D_x, D_u and D_y are used

    def dVsontag(self,curr_states):
        input_tensor = tf.reshape(curr_states, (curr_states.shape[0] , 1 , self.state_dim))
        two_times_x_times_P = tf.stack([ 2 * elem @ tf.convert_to_tensor(P, dtype = tf.float32) for elem in tf.unstack(input_tensor)])

        tildecurr_states = tf.stack([ elem @ D_x for elem in tf.unstack(input_tensor)])

        tildef_nn = tf.reshape(self.f_nn(tildecurr_states), (curr_states.shape[0] ,self.state_dim , 1))

        fnn = tf.stack([ D_y @ elem  for elem in tf.unstack(tildef_nn)])
    
        f = tf.reshape(fnn, (curr_states.shape[0] , self.state_dim, 1))
        a = tf.matmul(two_times_x_times_P, f) ### LfV

        tildeg = self.g_nn(tildecurr_states)
        g = tf.stack([ D_y @ elem @ D_u for elem in tf.unstack(tildeg)])
        dVdx_times_g = tf.matmul(two_times_x_times_P , g)

        b =  tf.gather(dVdx_times_g, [1], axis = 2)
        a_b = tf.concat([a,b],axis = 2)
        ab = tf.reshape(a_b, (curr_states.shape[0], 2))
        sontags = tf.reshape(tf.map_fn(lambda elem : phi(elem[0],elem[1]) , ab ), (curr_states.shape[0],1,1))
        LgVu = tf.matmul(b,sontags)
        return tf.reshape(a + LgVu,(curr_states.shape[0],1))
    
    ###get the value of sontag law
    def dVsontag_value(self,curr_states):
        input_tensor = tf.reshape(curr_states, (curr_states.shape[0] , 1 , self.state_dim))
        two_times_x_times_P = tf.stack([ 2 * elem @ tf.convert_to_tensor(P, dtype = tf.float32) for elem in tf.unstack(input_tensor)])

        tildecurr_states = tf.stack([ elem @ D_x for elem in tf.unstack(input_tensor)])

        tildef_nn = tf.reshape(self.f_nn(tildecurr_states), (curr_states.shape[0] ,self.state_dim , 1))

        fnn = tf.stack([ D_y @ elem  for elem in tf.unstack(tildef_nn)])
    
        f = tf.reshape(fnn, (curr_states.shape[0] , self.state_dim, 1))
        a = tf.matmul(two_times_x_times_P, f) ### LfV

        tildeg = self.g_nn(tildecurr_states)
        g = tf.stack([ D_y @ elem @ D_u for elem in tf.unstack(tildeg)])
        dVdx_times_g = tf.matmul(two_times_x_times_P , g)

        b =  tf.gather(dVdx_times_g, [1], axis = 2)
        a_b = tf.concat([a,b],axis = 2)
        ab = tf.reshape(a_b, (curr_states.shape[0], 2))
        sontags = tf.reshape(tf.map_fn(lambda elem : phi(elem[0],elem[1]) , ab ), (curr_states.shape[0],1,1))
       
        return sontags
    
     ###get the value of sontag law
    def dVsontag_value_CA0(self,curr_states):
        input_tensor = tf.reshape(curr_states, (curr_states.shape[0] , 1 , self.state_dim))
        #print('input_tensor',input_tensor)
        two_times_x_times_P = tf.stack([ 2 * elem @ tf.convert_to_tensor(P, dtype = tf.float32) for elem in tf.unstack(input_tensor)])
        #print('two_times_x_times_P',two_times_x_times_P)
        tildecurr_states = tf.stack([ elem @ D_x for elem in tf.unstack(input_tensor)])

        tildef_nn = tf.reshape(self.f_nn(tildecurr_states), (curr_states.shape[0] ,self.state_dim , 1))

        fnn = tf.stack([ D_y @ elem  for elem in tf.unstack(tildef_nn)])
    
        f = tf.reshape(fnn, (curr_states.shape[0] , self.state_dim, 1))
        a = tf.matmul(two_times_x_times_P, f) ### LfV

        tildeg = self.g_nn(tildecurr_states)
        g = tf.stack([ D_y @ elem @ D_u for elem in tf.unstack(tildeg)])
        dVdx_times_g = tf.matmul(two_times_x_times_P , g)

        b =  tf.gather(dVdx_times_g, [1], axis = 2)
       # print(b)
        a_b = tf.concat([a,b],axis = 2)
        ab = tf.reshape(a_b, (curr_states.shape[0], 2))
        sontags = tf.reshape(tf.map_fn(lambda elem : phi(elem[0],elem[1]) , ab ), (curr_states.shape[0],1,1))
        
        b2 = (2*1060*input_tensor[0,0,0] + (22+22)*input_tensor[0,0,1])*5
        b2 = tf.reshape(b2, (1 , 1 , 1))   ###get LgV1 for CA0
        a_b2 = tf.concat([a,b2],axis = 2)
        ab2 = tf.reshape(a_b2, (curr_states.shape[0], 2))
        sontags_CA0 = tf.reshape(tf.map_fn(lambda elem : phi_2(elem[0],elem[1]) , ab2 ), (curr_states.shape[0],1,1))
        return sontags_CA0
### this is dVdt for the NN model [\nabla V F_nn (x, sontag_nn(x))] but now remove states below \rho_s


    def dVsontag_modified(self,curr_states):
        input_tensor = tf.reshape(curr_states, (curr_states.shape[0] , 1 , self.state_dim))
        dVdt = tf.reshape(self.dVsontag(curr_states), (curr_states.shape[0],1,1))
        new_input = tf.concat([input_tensor, dVdt], axis = 2)
        inputs2 = tf.reshape(new_input , (curr_states.shape[0],3))
        x = tf.map_fn(lambda elem : modified_dVdt(elem[0],elem[1],elem[2]) , inputs2)
        return x

### this is dVdt for the FP model using NN sontang controller [\nabla V F (x, sontag_nn (x))] 

    def dVsontag_actual(self,curr_states):
        input_tensor = tf.reshape(curr_states, (curr_states.shape[0] , 1 , self.state_dim))
        two_times_x_times_P = tf.stack([ 2 * elem @ tf.convert_to_tensor(P, dtype = tf.float32) for elem in tf.unstack(input_tensor)])

        tildecurr_states = tf.stack([ elem @ D_x for elem in tf.unstack(input_tensor)])

        tildef_nn = tf.reshape(self.f_nn(tildecurr_states), (curr_states.shape[0] ,self.state_dim , 1))

        fnn = tf.stack([ D_y @ elem  for elem in tf.unstack(tildef_nn)])
        f = tf.reshape(fnn, (curr_states.shape[0] , self.state_dim, 1))
        a = tf.matmul(two_times_x_times_P, f) ### LfV
        tildeg = self.g_nn(tildecurr_states)
        g = tf.stack([ D_y @ elem @ D_u for elem in tf.unstack(tildeg)])
        dVdx_times_g = tf.matmul(two_times_x_times_P , g)
        b =  tf.gather(dVdx_times_g, [1], axis = 2)
        a_b = tf.concat([a,b],axis = 2)
        ab = tf.reshape(a_b, (curr_states.shape[0], 2))
        sontags = tf.reshape(tf.map_fn(lambda elem : phi(elem[0],elem[1]) , ab ), (curr_states.shape[0],1,1))
        concentrations = C_A0s + tf.zeros((curr_states.shape[0],1,1))
        inputs = tf.concat([input_tensor,concentrations,sontags], axis = 2 )
        actual_derivative = tf.map_fn( lambda x : CSTR_simulation_derivative2(x[0,0],x[0,1],x[0,2],x[0,3]), inputs )
        dVdt = tf.matmul(two_times_x_times_P,actual_derivative)
        return tf.reshape(dVdt, (curr_states.shape[0],1))

### this is dVdt for the FP model using NN sontang controller [\nabla V F (x, sontag_nn (x))] but now remove states below \rho_s

    def dVsontag_actual_modified(self,curr_states):
        input_tensor = tf.reshape(curr_states, (curr_states.shape[0] , 1 , self.state_dim))
        dVdt = tf.reshape(self.dVsontag_actual(curr_states), (curr_states.shape[0],1,1))
        new_input = tf.concat([input_tensor, dVdt], axis = 2)
        inputs2 = tf.reshape(new_input , (curr_states.shape[0],3))
        x = tf.map_fn(lambda elem : modified_dVdt(elem[0],elem[1],elem[2]) , inputs2)
        return x
    

        
def CSTR_simulation_derivative( C_A_initial, T_initial, C_A0, Q):
    
    C_A = C_A_initial + C_As
    T = T_initial + T_s
    
    dCAdt = F / V * (C_A0 - C_A) - k_0 * np.exp(-E / (R * T)) * C_A**2
    dTdt = F / V * (T_0 - T) -  delta_H / (rho_L * C_p) * k_0 * np.exp(-E / (R * T)) * C_A**2 + Q / (rho_L * C_p * V)
    
    return dCAdt, dTdt
   

import tensorflow as tf
from keras.losses import MeanSquaredError
from tensorflow.nn import relu


mse = tf.keras.losses.MeanSquaredError()

def custom_loss_function3(y_train, y_pred, model, X_batch, weight, threshold):
    X_batch_original = tf.convert_to_tensor(scaler_X.inverse_transform(X_batch), dtype = tf.float32)
    states = X_batch_original[:,0:2]
    dVdt = model.dVsontag_modified(states)
    reg_loss = tf.reduce_mean( relu(dVdt - threshold))
    loss1 =  mse(y_train,y_pred)
    loss2 =  reg_loss 
    return mse(y_train,y_pred) + weight * reg_loss, loss1, loss2





In [16]:
## training process

threshold = -10
weight = 0.001
num_epochs = 2
batchsize = 250
mse = tf.keras.losses.MeanSquaredError()
### this creates the model
model = ControlAffineNN(2,2,(10,10),(10,))

##
opt = tf.keras.optimizers.Adam(learning_rate=0.0007)
for epoch in range(num_epochs):
  for step in range(X_train.shape[0]//batchsize):
    start_idx = batchsize*step
    end_idx = batchsize*(step+1)
    X_batch = X_train[start_idx:end_idx]
    y_batch = y_train[start_idx:end_idx]
    with tf.GradientTape() as tape:
      pred = model(X_batch)
      loss , loss1 , loss2 = custom_loss_function3(y_batch, pred, model, X_batch, weight, threshold) 
    grads = tape.gradient(loss, model.trainable_variables)
    opt.apply_gradients(zip(grads, model.trainable_variables))
  print("Epoch : " , epoch, " Loss: " , loss, "Loss1", loss1.numpy(), "Loss2", loss2.numpy())

### save weights




250
250
250
250
250
250
250
250
250
250
250
250
250
250
250
250
250
250
250
250
250
250
250
250
250
250
250
250
250
250
250
250
250
250
250
Epoch :  0  Loss:  tf.Tensor(1.1400459, shape=(), dtype=float32) Loss1 1.1208928 Loss2 19.153135
250
250
250
250
250
250
250
250
250
250
250
250
250
250
250
250
250
250
250
250
250
250
250
250
250
250
250
250
250
250
250
250
250
250
250
Epoch :  1  Loss:  tf.Tensor(0.8776022, shape=(), dtype=float32) Loss1 0.87709314 Loss2 0.509059


In [17]:
model.load_weights("test_new_region3") ###0.0005 for 200 epoch, then 

print(mse(model(X_train),y_train)) ###the training error
pred = model(X_test)
print(mse(pred,y_test))  ###the testing error

8750
tf.Tensor(5.337881884770468e-05, shape=(), dtype=float64)
3750
tf.Tensor(5.510313349077478e-05, shape=(), dtype=float64)


# Test the performance of LSNN

In [18]:
#sontag law using LSNN
NN_input_tf = tf.convert_to_tensor(NN_input, dtype = tf.float32) ### convert the array to tensor

print('NN_input_tf', NN_input_tf)  ###get the input in real value

states = NN_input_tf[:,0:2]
print('states',states)
dVdt = model.dVsontag(states) ###using state to calculate the dVdt for the NN model using LSNN, 
print('dVdt', dVdt)

k = 0
for i in range(12500):   ###tell the number of initial states which dvdt is positive
    if dVdt[i] <0:
        k = k+1
print(k)

NN_input_tf tf.Tensor(
[[ 1.4677215e+00 -7.5417725e+01 -3.5000000e+00 -5.0000000e+05]
 [ 1.5436709e+00 -7.5417725e+01 -3.5000000e+00 -5.0000000e+05]
 [ 1.6196202e+00 -7.5417725e+01 -3.5000000e+00 -5.0000000e+05]
 ...
 [-1.4183544e+00  7.2683548e+01  3.5000000e+00  5.0000000e+05]
 [-1.3424051e+00  7.2683548e+01  3.5000000e+00  5.0000000e+05]
 [-1.5702531e+00  7.6481010e+01  3.5000000e+00  5.0000000e+05]], shape=(12500, 4), dtype=float32)
states tf.Tensor(
[[  1.4677215 -75.417725 ]
 [  1.5436709 -75.417725 ]
 [  1.6196202 -75.417725 ]
 ...
 [ -1.4183544  72.68355  ]
 [ -1.3424051  72.68355  ]
 [ -1.5702531  76.48101  ]], shape=(12500, 2), dtype=float32)
dVdt tf.Tensor(
[[ -861.1405]
 [ -861.9755]
 [ -740.9227]
 ...
 [-4552.48  ]
 [-3497.2004]
 [-6411.9463]], shape=(12500, 1), dtype=float32)
12500


In [36]:
#sontag law using LSNN
NN_input_tf = tf.convert_to_tensor(NN_input, dtype = tf.float32) ### convert the array to tensor

print('NN_input_tf', NN_input_tf)  ###get the input in real value

states = NN_input_tf[:,0:2]
print('states',states)
dVdt = model.dVsontag_actual(states) ###using state to calculate the dVdt for the FP model using LSNN, 
print('dVdt', dVdt)

k = 0
for i in range(12500):   ###tell the number of initial states which dvdt is positive
    if dVdt[i] <0:
        k = k+1
    else:
        print(dVdt[i])
print(k)

NN_input_tf tf.Tensor(
[[ 1.4677215e+00 -7.5417725e+01 -3.5000000e+00 -5.0000000e+05]
 [ 1.5436709e+00 -7.5417725e+01 -3.5000000e+00 -5.0000000e+05]
 [ 1.6196202e+00 -7.5417725e+01 -3.5000000e+00 -5.0000000e+05]
 ...
 [-1.4183544e+00  7.2683548e+01  3.5000000e+00  5.0000000e+05]
 [-1.3424051e+00  7.2683548e+01  3.5000000e+00  5.0000000e+05]
 [-1.5702531e+00  7.6481010e+01  3.5000000e+00  5.0000000e+05]], shape=(12500, 4), dtype=float32)
states tf.Tensor(
[[  1.4677215 -75.417725 ]
 [  1.5436709 -75.417725 ]
 [  1.6196202 -75.417725 ]
 ...
 [ -1.4183544  72.68355  ]
 [ -1.3424051  72.68355  ]
 [ -1.5702531  76.48101  ]], shape=(12500, 2), dtype=float32)
dVdt tf.Tensor(
[[ -961.8031 ]
 [ -937.50995]
 [ -791.9447 ]
 ...
 [-4700.28   ]
 [-3836.7888 ]
 [-6615.0884 ]], shape=(12500, 1), dtype=float32)
tf.Tensor([45.116333], shape=(1,), dtype=float32)
tf.Tensor([34.97412], shape=(1,), dtype=float32)
tf.Tensor([47.183105], shape=(1,), dtype=float32)
tf.Tensor([109.09277], shape=(1,), dtype=flo

# Obtain the state trajectory under NN-based Sontag controller

In [23]:
def CSTR_simulation_update( C_A_initial, T_initial, C_A0, Q):  ###update the state values 
      
    C_A = C_A_initial + C_As
    T = T_initial + T_s
    #print(C_A,T)
  
    dCAdt = F / V * (C_A0 - C_A) - k_0 * np.exp(-E / (R * T)) * C_A**2
    dTdt = F / V * (T_0 - T) -  delta_H / (rho_L * C_p) * k_0 * np.exp(-E / (R * T)) * C_A**2 + Q / (rho_L * C_p * V)
    
    delta = 0.001  ###the interation time

    C_A = C_A + dCAdt*delta
    T = T + dTdt*delta
   
    C_A = C_A - C_As
    T = T - T_s
    return np.array([C_A, T, dCAdt,dTdt])

In [25]:
###get trajectory data for ploting using LSNN to get sontag law, two sontag laws
update_states = [[0.84,      -59]]

update_states_list = list()
#update_states_list.append(update_states)


for k in range(4000):
    update_states = tf.convert_to_tensor(update_states, dtype = tf.float32) ###convert the state to tensor
    print(update_states)
    Sontag_value = tf.reshape(model.dVsontag_value(update_states),(1))  ### get the sontag law
    Sontag_value_CA0 = tf.reshape(model.dVsontag_value_CA0(update_states),(1))  ### get the sontag law
    input_vector = list() ###generate the empty list
   
    state = update_states[0].numpy()
    print("state", state)
    inputs = Sontag_value.numpy()
    print('input',inputs)
    inputs_CA0 = Sontag_value_CA0.numpy() + 4
    print('input_CA0',inputs_CA0)
    collected_data = CSTR_simulation_update(state[0], state[1], inputs_CA0, inputs) ### C_A, T, dC, dT, note C_A and T are deviation
        #print('collected_date',collected_data)

    input_vector.append(collected_data)  ###convert the collected data to list

    input_vector = np.array(input_vector) ###convert the list to numpy array
    update_states = input_vector[-4:,:2]  ##3get the update states
    print(k, update_states)
    update_states_list.append(update_states[0])
print(update_states)


tf.Tensor([[  0.84 -59.  ]], shape=(1, 2), dtype=float32)
state [  0.84 -59.  ]
input [0.]
input_CA0 [7.5]
0 [[[  0.86195064]
  [-59.135376  ]]]
tf.Tensor(
[[[  0.86195064]
  [-59.135376  ]]], shape=(1, 2, 1), dtype=float32)
state [[  0.86195064]
 [-59.135376  ]]
input [0.]
input_CA0 [7.5]
1 [[[  0.8837776]
  [-59.26938  ]]]
tf.Tensor(
[[[  0.8837776]
  [-59.26938  ]]], shape=(1, 2, 1), dtype=float32)
state [[  0.8837776]
 [-59.26938  ]]
input [125.750725]
input_CA0 [7.5]
2 [[[  0.90548134]
  [-59.40149   ]]]
tf.Tensor(
[[[  0.90548134]
  [-59.40149   ]]], shape=(1, 2, 1), dtype=float32)
state [[  0.90548134]
 [-59.40149   ]]
input [2141.0195]
input_CA0 [7.5]
3 [[[  0.92706275]
  [-59.5235    ]]]
tf.Tensor(
[[[  0.92706275]
  [-59.5235    ]]], shape=(1, 2, 1), dtype=float32)
state [[  0.92706275]
 [-59.5235    ]]
input [4168.2544]
input_CA0 [7.5]
4 [[[  0.94852185]
  [-59.635406  ]]]
tf.Tensor(
[[[  0.94852185]
  [-59.635406  ]]], shape=(1, 2, 1), dtype=float32)
state [[  0.94852185]
 

state [[  1.1584504]
 [-56.04245  ]]
input [48084.59]
input_CA0 [7.5]
58 [[[  1.1781018]
  [-55.94928  ]]]
tf.Tensor(
[[[  1.1781018]
  [-55.94928  ]]], shape=(1, 2, 1), dtype=float32)
state [[  1.1781018]
 [-55.94928  ]]
input [53576.49]
input_CA0 [0.5]
59 [[[  1.1626148]
  [-55.83078  ]]]
tf.Tensor(
[[[  1.1626148]
  [-55.83078  ]]], shape=(1, 2, 1), dtype=float32)
state [[  1.1626148]
 [-55.83078  ]]
input [50241.133]
input_CA0 [0.5]
60 [[[  1.1472147]
  [-55.727783 ]]]
tf.Tensor(
[[[  1.1472147]
  [-55.727783 ]]], shape=(1, 2, 1), dtype=float32)
state [[  1.1472147]
 [-55.727783 ]]
input [47120.145]
input_CA0 [7.5]
61 [[[  1.1669025]
  [-55.639374 ]]]
tf.Tensor(
[[[  1.1669025]
  [-55.639374 ]]], shape=(1, 2, 1), dtype=float32)
state [[  1.1669025]
 [-55.639374 ]]
input [52467.35]
input_CA0 [0.5]
62 [[[  1.1514518]
  [-55.526245 ]]]
tf.Tensor(
[[[  1.1514518]
  [-55.526245 ]]], shape=(1, 2, 1), dtype=float32)
state [[  1.1514518]
 [-55.526245 ]]
input [49188.793]
input_CA0 [7.5]
63

state [[  1.0347493]
 [-48.91754  ]]
input [58937.57]
input_CA0 [0.5]
123 [[[  1.0193057]
  [-48.777466 ]]]
tf.Tensor(
[[[  1.0193057]
  [-48.777466 ]]], shape=(1, 2, 1), dtype=float32)
state [[  1.0193057]
 [-48.777466 ]]
input [54641.535]
input_CA0 [0.5]
124 [[[  1.0039504]
  [-48.657257 ]]]
tf.Tensor(
[[[  1.0039504]
  [-48.657257 ]]], shape=(1, 2, 1), dtype=float32)
state [[  1.0039504]
 [-48.657257 ]]
input [50715.145]
input_CA0 [7.5]
125 [[[  1.0236855]
  [-48.55533  ]]]
tf.Tensor(
[[[  1.0236855]
  [-48.55533  ]]], shape=(1, 2, 1), dtype=float32)
state [[  1.0236855]
 [-48.55533  ]]
input [57874.285]
input_CA0 [0.5]
126 [[[  1.0082669]
  [-48.420166 ]]]
tf.Tensor(
[[[  1.0082669]
  [-48.420166 ]]], shape=(1, 2, 1), dtype=float32)
state [[  1.0082669]
 [-48.420166 ]]
input [53646.266]
input_CA0 [0.5]
127 [[[  0.9929373]
  [-48.304565 ]]]
tf.Tensor(
[[[  0.9929373]
  [-48.304565 ]]], shape=(1, 2, 1), dtype=float32)
state [[  0.9929373]
 [-48.304565 ]]
input [49775.418]
input_CA0 [

state [[  0.83668375]
 [-40.784546  ]]
input [52241.016]
input_CA0 [7.5]
186 [[[  0.8563876]
  [-40.67218  ]]]
tf.Tensor(
[[[  0.8563876]
  [-40.67218  ]]], shape=(1, 2, 1), dtype=float32)
state [[  0.8563876]
 [-40.67218  ]]
input [60829.16]
input_CA0 [0.5]
187 [[[  0.8409178]
  [-40.51944  ]]]
tf.Tensor(
[[[  0.8409178]
  [-40.51944  ]]], shape=(1, 2, 1), dtype=float32)
state [[  0.8409178]
 [-40.51944  ]]
input [56101.82]
input_CA0 [7.5]
188 [[[  0.86054134]
  [-40.388733  ]]]
tf.Tensor(
[[[  0.86054134]
  [-40.388733  ]]], shape=(1, 2, 1), dtype=float32)
state [[  0.86054134]
 [-40.388733  ]]
input [64690.797]
input_CA0 [0.5]
189 [[[  0.8449874]
  [-40.21753  ]]]
tf.Tensor(
[[[  0.8449874]
  [-40.21753  ]]], shape=(1, 2, 1), dtype=float32)
state [[  0.8449874]
 [-40.21753  ]]
input [59572.863]
input_CA0 [0.5]
190 [[[  0.82952404]
  [-40.069977  ]]]
tf.Tensor(
[[[  0.82952404]
  [-40.069977  ]]], shape=(1, 2, 1), dtype=float32)
state [[  0.82952404]
 [-40.069977  ]]
input [55079.535

state [[  0.69933105]
 [-32.763123  ]]
input [55357.832]
input_CA0 [0.5]
249 [[[  0.6835718]
  [-32.620117 ]]]
tf.Tensor(
[[[  0.6835718]
  [-32.620117 ]]], shape=(1, 2, 1), dtype=float32)
state [[  0.6835718]
 [-32.620117 ]]
input [49619.785]
input_CA0 [0.5]
250 [[[  0.6679194]
  [-32.50406  ]]]
tf.Tensor(
[[[  0.6679194]
  [-32.50406  ]]], shape=(1, 2, 1), dtype=float32)
state [[  0.6679194]
 [-32.50406  ]]
input [44823.258]
input_CA0 [7.5]
251 [[[  0.6873791]
  [-32.41104  ]]]
tf.Tensor(
[[[  0.6873791]
  [-32.41104  ]]], shape=(1, 2, 1), dtype=float32)
state [[  0.6873791]
 [-32.41104  ]]
input [52800.043]
input_CA0 [0.5]
252 [[[  0.6716471]
  [-32.279236 ]]]
tf.Tensor(
[[[  0.6716471]
  [-32.279236 ]]], shape=(1, 2, 1), dtype=float32)
state [[  0.6716471]
 [-32.279236 ]]
input [47414.953]
input_CA0 [0.5]
253 [[[  0.6560247]
  [-32.172943 ]]]
tf.Tensor(
[[[  0.6560247]
  [-32.172943 ]]], shape=(1, 2, 1), dtype=float32)
state [[  0.6560247]
 [-32.172943 ]]
input [42877.285]
input_CA

...

state [[ 0.14981604]
 [-7.9520874 ]]
input [5052.2812]
input_CA0 [7.5]
3764 [[[ 0.16803598]
  [-7.963318  ]]]
tf.Tensor(
[[[ 0.16803598]
  [-7.963318  ]]], shape=(1, 2, 1), dtype=float32)
state [[ 0.16803598]
 [-7.963318  ]]
input [6557.143]
input_CA0 [0.5]
3765 [[[ 0.15101576]
  [-7.960541  ]]]
tf.Tensor(
[[[ 0.15101576]
  [-7.960541  ]]], shape=(1, 2, 1), dtype=float32)
state [[ 0.15101576]
 [-7.960541  ]]
input [5164.1636]
input_CA0 [7.5]
3766 [[[ 0.1692226]
  [-7.970886 ]]]
tf.Tensor(
[[[ 0.1692226]
  [-7.970886 ]]], shape=(1, 2, 1), dtype=float32)
state [[ 0.1692226]
 [-7.970886 ]]
input [6638.406]
input_CA0 [0.5]
3767 [[[ 0.15218902]
  [-7.967346  ]]]
tf.Tensor(
[[[ 0.15218902]
  [-7.967346  ]]], shape=(1, 2, 1), dtype=float32)
state [[ 0.15218902]
 [-7.967346  ]]
input [5273.251]
input_CA0 [7.5]
3768 [[[ 0.1703825]
  [-7.9768066]]]
tf.Tensor(
[[[ 0.1703825]
  [-7.9768066]]], shape=(1, 2, 1), dtype=float32)
state [[ 0.1703825]
 [-7.9768066]]
input [6711.1553]
input_CA0 [0.5]
3769

state [[ 0.16657925]
 [-7.9565125 ]]
input [6455.9336]
input_CA0 [0.5]
3831 [[[ 0.14957619]
  [-7.954712  ]]]
tf.Tensor(
[[[ 0.14957619]
  [-7.954712  ]]], shape=(1, 2, 1), dtype=float32)
state [[ 0.14957619]
 [-7.954712  ]]
input [5029.51]
input_CA0 [7.5]
3832 [[[ 0.16780043]
  [-7.966156  ]]]
tf.Tensor(
[[[ 0.16780043]
  [-7.966156  ]]], shape=(1, 2, 1), dtype=float32)
state [[ 0.16780043]
 [-7.966156  ]]
input [6546.9336]
input_CA0 [0.5]
3833 [[[ 0.15078425]
  [-7.963562  ]]]
tf.Tensor(
[[[ 0.15078425]
  [-7.963562  ]]], shape=(1, 2, 1), dtype=float32)
state [[ 0.15078425]
 [-7.963562  ]]
input [5142.365]
input_CA0 [7.5]
3834 [[[ 0.16899514]
  [-7.974121  ]]]
tf.Tensor(
[[[ 0.16899514]
  [-7.974121  ]]], shape=(1, 2, 1), dtype=float32)
state [[ 0.16899514]
 [-7.974121  ]]
input [6630.854]
input_CA0 [0.5]
3835 [[[ 0.15196586]
  [-7.970764  ]]]
tf.Tensor(
[[[ 0.15196586]
  [-7.970764  ]]], shape=(1, 2, 1), dtype=float32)
state [[ 0.15196586]
 [-7.970764  ]]
input [5252.499]
input_CA0 

state [[ 0.17262077]
 [-7.9838867 ]]
input [6824.9946]
input_CA0 [0.5]
3876 [[[ 0.15554595]
  [-7.9782715 ]]]
tf.Tensor(
[[[ 0.15554595]
  [-7.9782715 ]]], shape=(1, 2, 1), dtype=float32)
state [[ 0.15554595]
 [-7.9782715 ]]
input [5581.454]
input_CA0 [7.5]
3877 [[[ 0.17369819]
  [-7.985138  ]]]
tf.Tensor(
[[[ 0.17369819]
  [-7.985138  ]]], shape=(1, 2, 1), dtype=float32)
state [[ 0.17369819]
 [-7.985138  ]]
input [6862.074]
input_CA0 [0.5]
3878 [[[ 0.15660954]
  [-7.978943  ]]]
tf.Tensor(
[[[ 0.15660954]
  [-7.978943  ]]], shape=(1, 2, 1), dtype=float32)
state [[ 0.15660954]
 [-7.978943  ]]
input [5676.9907]
input_CA0 [7.5]
3879 [[[ 0.17474794]
  [-7.984955  ]]]
tf.Tensor(
[[[ 0.17474794]
  [-7.984955  ]]], shape=(1, 2, 1), dtype=float32)
state [[ 0.17474794]
 [-7.984955  ]]
input [6882.432]
input_CA0 [0.5]
3880 [[[ 0.15764499]
  [-7.9782104 ]]]
tf.Tensor(
[[[ 0.15764499]
  [-7.9782104 ]]], shape=(1, 2, 1), dtype=float32)
state [[ 0.15764499]
 [-7.9782104 ]]
input [5768.418]
input_CA0

state [[ 0.1610539]
 [-7.972473 ]]
input [6056.5117]
input_CA0 [7.5]
3922 [[[ 0.17913055]
  [-7.9749146 ]]]
tf.Tensor(
[[[ 0.17913055]
  [-7.9749146 ]]], shape=(1, 2, 1), dtype=float32)
state [[ 0.17913055]
 [-7.9749146 ]]
input [6680.86]
input_CA0 [0.5]
3923 [[[ 0.16196513]
  [-7.9670715 ]]]
tf.Tensor(
[[[ 0.16196513]
  [-7.9670715 ]]], shape=(1, 2, 1), dtype=float32)
state [[ 0.16196513]
 [-7.9670715 ]]
input [6127.1704]
input_CA0 [7.5]
3924 [[[ 0.18002772]
  [-7.96875   ]]]
tf.Tensor(
[[[ 0.18002772]
  [-7.96875   ]]], shape=(1, 2, 1), dtype=float32)
state [[ 0.18002772]
 [-7.96875   ]]
input [6509.5195]
input_CA0 [0.5]
3925 [[[ 0.162848]
  [-7.961212]]]
tf.Tensor(
[[[ 0.162848]
  [-7.961212]]], shape=(1, 2, 1), dtype=float32)
state [[ 0.162848]
 [-7.961212]]
input [6192.4775]
input_CA0 [7.5]
3926 [[[ 0.18089676]
  [-7.962158  ]]]
tf.Tensor(
[[[ 0.18089676]
  [-7.962158  ]]], shape=(1, 2, 1), dtype=float32)
state [[ 0.18089676]
 [-7.962158  ]]
input [6261.3726]
input_CA0 [0.5]
3927 

state [[ 0.16558433]
 [-7.9431458 ]]
input [6373.459]
input_CA0 [0.5]
3967 [[[ 0.14859009]
  [-7.9419556 ]]]
tf.Tensor(
[[[ 0.14859009]
  [-7.9419556 ]]], shape=(1, 2, 1), dtype=float32)
state [[ 0.14859009]
 [-7.9419556 ]]
input [4937.7886]
input_CA0 [7.5]
3968 [[[ 0.16682315]
  [-7.954071  ]]]
tf.Tensor(
[[[ 0.16682315]
  [-7.954071  ]]], shape=(1, 2, 1), dtype=float32)
state [[ 0.16682315]
 [-7.954071  ]]
input [6468.489]
input_CA0 [0.5]
3969 [[[ 0.14981604]
  [-7.9520874 ]]]
tf.Tensor(
[[[ 0.14981604]
  [-7.9520874 ]]], shape=(1, 2, 1), dtype=float32)
state [[ 0.14981604]
 [-7.9520874 ]]
input [5052.2812]
input_CA0 [7.5]
3970 [[[ 0.16803598]
  [-7.963318  ]]]
tf.Tensor(
[[[ 0.16803598]
  [-7.963318  ]]], shape=(1, 2, 1), dtype=float32)
state [[ 0.16803598]
 [-7.963318  ]]
input [6557.143]
input_CA0 [0.5]
3971 [[[ 0.15101576]
  [-7.960541  ]]]
tf.Tensor(
[[[ 0.15101576]
  [-7.960541  ]]], shape=(1, 2, 1), dtype=float32)
state [[ 0.15101576]
 [-7.960541  ]]
input [5164.1636]
input_CA

In [26]:
##right down
np.savetxt("trajectory_FCU0_new.txt",    np.array(update_states_list).reshape(-1,2), fmt="%f",  delimiter=" ")

In [27]:
###get trajectory data for ploting using LSNN to get sontag law, two sontag laws
update_states = [[1.1,      -29]]

update_states_list = list()
#update_states_list.append(update_states)


for k in range(4000):
    update_states = tf.convert_to_tensor(update_states, dtype = tf.float32) ###convert the state to tensor
    print(update_states)
    Sontag_value = tf.reshape(model.dVsontag_value(update_states),(1))  ### get the sontag law
    Sontag_value_CA0 = tf.reshape(model.dVsontag_value_CA0(update_states),(1))  ### get the sontag law
    input_vector = list() ###generate the empty list
   
    state = update_states[0].numpy()
    print("state", state)
    inputs = Sontag_value.numpy()
    print('input',inputs)
    inputs_CA0 = Sontag_value_CA0.numpy() + 4
    print('input_CA0',inputs_CA0)
    collected_data = CSTR_simulation_update(state[0], state[1], inputs_CA0, inputs) ### C_A, T, dC, dT, note C_A and T are deviation
        #print('collected_date',collected_data)

    input_vector.append(collected_data)  ###convert the collected data to list

    input_vector = np.array(input_vector) ###convert the list to numpy array
    update_states = input_vector[-4:,:2]  ##3get the update states
    print(k, update_states)
    update_states_list.append(update_states[0])
print(update_states)


tf.Tensor([[  1.1 -29. ]], shape=(1, 2), dtype=float32)
state [  1.1 -29. ]
input [-0.]
input_CA0 [0.5]
0 [[[  1.0794201]
  [-28.97519  ]]]
tf.Tensor(
[[[  1.0794201]
  [-28.97519  ]]], shape=(1, 2, 1), dtype=float32)
state [[  1.0794201]
 [-28.97519  ]]
input [-0.]
input_CA0 [0.5]
1 [[[  1.0590401]
  [-28.955353 ]]]
tf.Tensor(
[[[  1.0590401]
  [-28.955353 ]]], shape=(1, 2, 1), dtype=float32)
state [[  1.0590401]
 [-28.955353 ]]
input [-0.]
input_CA0 [0.5]
2 [[[  1.0388591]
  [-28.94043  ]]]
tf.Tensor(
[[[  1.0388591]
  [-28.94043  ]]], shape=(1, 2, 1), dtype=float32)
state [[  1.0388591]
 [-28.94043  ]]
input [-0.]
input_CA0 [0.5]
3 [[[  1.0188763]
  [-28.93042  ]]]
tf.Tensor(
[[[  1.0188763]
  [-28.93042  ]]], shape=(1, 2, 1), dtype=float32)
state [[  1.0188763]
 [-28.93042  ]]
input [-0.]
input_CA0 [0.5]
4 [[[  0.9990907]
  [-28.925323 ]]]
tf.Tensor(
[[[  0.9990907]
  [-28.925323 ]]], shape=(1, 2, 1), dtype=float32)
state [[  0.9990907]
 [-28.925323 ]]
input [-0.]
input_CA0 [0.5]
5

state [[  0.53163147]
 [-25.869843  ]]
input [37524.996]
input_CA0 [7.5]
63 [[[  0.5507953]
  [-25.792938 ]]]
tf.Tensor(
[[[  0.5507953]
  [-25.792938 ]]], shape=(1, 2, 1), dtype=float32)
state [[  0.5507953]
 [-25.792938 ]]
input [46309.414]
input_CA0 [0.5]
64 [[[  0.5347519]
  [-25.672821 ]]]
tf.Tensor(
[[[  0.5347519]
  [-25.672821 ]]], shape=(1, 2, 1), dtype=float32)
state [[  0.5347519]
 [-25.672821 ]]
input [39948.387]
input_CA0 [0.5]
65 [[[  0.5188353]
  [-25.58319  ]]]
tf.Tensor(
[[[  0.5188353]
  [-25.58319  ]]], shape=(1, 2, 1), dtype=float32)
state [[  0.5188353]
 [-25.58319  ]]
input [34957.53]
input_CA0 [7.5]
66 [[[  0.5380523]
  [-25.51828  ]]]
tf.Tensor(
[[[  0.5380523]
  [-25.51828  ]]], shape=(1, 2, 1), dtype=float32)
state [[  0.5380523]
 [-25.51828  ]]
input [42531.133]
input_CA0 [0.5]
67 [[[  0.52206373]
  [-25.415466  ]]]
tf.Tensor(
[[[  0.52206373]
  [-25.415466  ]]], shape=(1, 2, 1), dtype=float32)
state [[  0.52206373]
 [-25.415466  ]]
input [36944.652]
input_CA

state [[  0.41330743]
 [-20.212372  ]]
input [30530.16]
input_CA0 [7.5]
127 [[[  0.43217754]
  [-20.149933  ]]]
tf.Tensor(
[[[  0.43217754]
  [-20.149933  ]]], shape=(1, 2, 1), dtype=float32)
state [[  0.43217754]
 [-20.149933  ]]
input [40030.75]
input_CA0 [0.5]
128 [[[  0.41582608]
  [-20.040375  ]]]
tf.Tensor(
[[[  0.41582608]
  [-20.040375  ]]], shape=(1, 2, 1), dtype=float32)
state [[  0.41582608]
 [-20.040375  ]]
input [32679.586]
input_CA0 [7.5]
129 [[[  0.43462038]
  [-19.96637   ]]]
tf.Tensor(
[[[  0.43462038]
  [-19.96637   ]]], shape=(1, 2, 1), dtype=float32)
state [[  0.43462038]
 [-19.96637   ]]
input [44486.8]
input_CA0 [0.5]
130 [[[  0.41818976]
  [-19.835083  ]]]
tf.Tensor(
[[[  0.41818976]
  [-19.835083  ]]], shape=(1, 2, 1), dtype=float32)
state [[  0.41818976]
 [-19.835083  ]]
input [35479.3]
input_CA0 [0.5]
131 [[[  0.40190005]
  [-19.746368  ]]]
tf.Tensor(
[[[  0.40190005]
  [-19.746368  ]]], shape=(1, 2, 1), dtype=float32)
state [[  0.40190005]
 [-19.746368  ]]
in

state [[  0.30983973]
 [-15.276306  ]]
input [22598.68]
input_CA0 [7.5]
191 [[[  0.32842326]
  [-15.23288   ]]]
tf.Tensor(
[[[  0.32842326]
  [-15.23288   ]]], shape=(1, 2, 1), dtype=float32)
state [[  0.32842326]
 [-15.23288   ]]
input [30215.332]
input_CA0 [0.5]
192 [[[  0.3117745]
  [-15.14975  ]]]
tf.Tensor(
[[[  0.3117745]
  [-15.14975  ]]], shape=(1, 2, 1), dtype=float32)
state [[  0.3117745]
 [-15.14975  ]]
input [23673.639]
input_CA0 [7.5]
193 [[[  0.33029652]
  [-15.099731  ]]]
tf.Tensor(
[[[  0.33029652]
  [-15.099731  ]]], shape=(1, 2, 1), dtype=float32)
state [[  0.33029652]
 [-15.099731  ]]
input [32875.625]
input_CA0 [0.5]
194 [[[  0.3135841]
  [-15.003052 ]]]
tf.Tensor(
[[[  0.3135841]
  [-15.003052 ]]], shape=(1, 2, 1), dtype=float32)
state [[  0.3135841]
 [-15.003052 ]]
input [24976.646]
input_CA0 [0.5]
195 [[[  0.29703927]
  [-14.945251  ]]]
tf.Tensor(
[[[  0.29703927]
  [-14.945251  ]]], shape=(1, 2, 1), dtype=float32)
state [[  0.29703927]
 [-14.945251  ]]
input [20

state [[  0.24398923]
 [-12.137817  ]]
input [15024.991]
input_CA0 [7.5]
256 [[[  0.26238203]
  [-12.116974  ]]]
tf.Tensor(
[[[  0.26238203]
  [-12.116974  ]]], shape=(1, 2, 1), dtype=float32)
state [[  0.26238203]
 [-12.116974  ]]
input [20651.928]
input_CA0 [0.5]
257 [[[  0.24553895]
  [-12.064728  ]]]
tf.Tensor(
[[[  0.24553895]
  [-12.064728  ]]], shape=(1, 2, 1), dtype=float32)
state [[  0.24553895]
 [-12.064728  ]]
input [15540.664]
input_CA0 [7.5]
258 [[[  0.26388884]
  [-12.040283  ]]]
tf.Tensor(
[[[  0.26388884]
  [-12.040283  ]]], shape=(1, 2, 1), dtype=float32)
state [[  0.26388884]
 [-12.040283  ]]
input [21981.418]
input_CA0 [0.5]
259 [[[  0.24700165]
  [-11.980835  ]]]
tf.Tensor(
[[[  0.24700165]
  [-11.980835  ]]], shape=(1, 2, 1), dtype=float32)
state [[  0.24700165]
 [-11.980835  ]]
input [16111.748]
input_CA0 [7.5]
260 [[[  0.26530623]
  [-11.952423  ]]]
tf.Tensor(
[[[  0.26530623]
  [-11.952423  ]]], shape=(1, 2, 1), dtype=float32)
state [[  0.26530623]
 [-11.952423 

...

state [[ 0.17756772]
 [-7.982361  ]]
input [6839.4106]
input_CA0 [0.5]
3811 [[[ 0.1604259]
  [-7.974579 ]]]
tf.Tensor(
[[[ 0.1604259]
  [-7.974579 ]]], shape=(1, 2, 1), dtype=float32)
state [[ 0.1604259]
 [-7.974579 ]]
input [6005.6006]
input_CA0 [7.5]
3812 [[[ 0.17851162]
  [-7.9775085 ]]]
tf.Tensor(
[[[ 0.17851162]
  [-7.9775085 ]]], shape=(1, 2, 1), dtype=float32)
state [[ 0.17851162]
 [-7.9775085 ]]
input [6755.2725]
input_CA0 [0.5]
3813 [[[ 0.1613555]
  [-7.969635 ]]]
tf.Tensor(
[[[ 0.1613555]
  [-7.969635 ]]], shape=(1, 2, 1), dtype=float32)
state [[ 0.1613555]
 [-7.969635 ]]
input [6079.5703]
input_CA0 [7.5]
3814 [[[ 0.17942715]
  [-7.9718018 ]]]
tf.Tensor(
[[[ 0.17942715]
  [-7.9718018 ]]], shape=(1, 2, 1), dtype=float32)
state [[ 0.17942715]
 [-7.9718018 ]]
input [6622.718]
input_CA0 [0.5]
3815 [[[ 0.16225672]
  [-7.9640503 ]]]
tf.Tensor(
[[[ 0.16225672]
  [-7.9640503 ]]], shape=(1, 2, 1), dtype=float32)
state [[ 0.16225672]
 [-7.9640503 ]]
input [6148.315]
input_CA0 [7.5]
381

state [[ 0.1640997]
 [-7.946869 ]]
input [6273.8965]
input_CA0 [7.5]
3855 [[[ 0.18212676]
  [-7.9467773 ]]]
tf.Tensor(
[[[ 0.18212676]
  [-7.9467773 ]]], shape=(1, 2, 1), dtype=float32)
state [[ 0.18212676]
 [-7.9467773 ]]
input [5589.301]
input_CA0 [0.5]
3856 [[[ 0.16491103]
  [-7.942047  ]]]
tf.Tensor(
[[[ 0.16491103]
  [-7.942047  ]]], shape=(1, 2, 1), dtype=float32)
state [[ 0.16491103]
 [-7.942047  ]]
input [6326.371]
input_CA0 [0.5]
3857 [[[ 0.14792538]
  [-7.9413147 ]]]
tf.Tensor(
[[[ 0.14792538]
  [-7.9413147 ]]], shape=(1, 2, 1), dtype=float32)
state [[ 0.14792538]
 [-7.9413147 ]]
input [4875.04]
input_CA0 [7.5]
3858 [[[ 0.16616702]
  [-7.9539795 ]]]
tf.Tensor(
[[[ 0.16616702]
  [-7.9539795 ]]], shape=(1, 2, 1), dtype=float32)
state [[ 0.16616702]
 [-7.9539795 ]]
input [6425.543]
input_CA0 [0.5]
3859 [[[ 0.14916873]
  [-7.9524536 ]]]
tf.Tensor(
[[[ 0.14916873]
  [-7.9524536 ]]], shape=(1, 2, 1), dtype=float32)
state [[ 0.14916873]
 [-7.9524536 ]]
input [4991.317]
input_CA0 [7.

state [[ 0.15196729]
 [-7.9707947 ]]
input [5252.633]
input_CA0 [7.5]
3899 [[[ 0.17016482]
  [-7.9804688 ]]]
tf.Tensor(
[[[ 0.17016482]
  [-7.9804688 ]]], shape=(1, 2, 1), dtype=float32)
state [[ 0.17016482]
 [-7.9804688 ]]
input [6706.7964]
input_CA0 [0.5]
3900 [[[ 0.15312195]
  [-7.9763794 ]]]
tf.Tensor(
[[[ 0.15312195]
  [-7.9763794 ]]], shape=(1, 2, 1), dtype=float32)
state [[ 0.15312195]
 [-7.9763794 ]]
input [5359.8057]
input_CA0 [7.5]
3901 [[[ 0.17130613]
  [-7.985199  ]]]
tf.Tensor(
[[[ 0.17130613]
  [-7.985199  ]]], shape=(1, 2, 1), dtype=float32)
state [[ 0.17130613]
 [-7.985199  ]]
input [6773.151]
input_CA0 [0.5]
3902 [[[ 0.15424967]
  [-7.980377  ]]]
tf.Tensor(
[[[ 0.15424967]
  [-7.980377  ]]], shape=(1, 2, 1), dtype=float32)
state [[ 0.15424967]
 [-7.980377  ]]
input [5463.8154]
input_CA0 [7.5]
3903 [[[ 0.17242002]
  [-7.988312  ]]]
tf.Tensor(
[[[ 0.17242002]
  [-7.988312  ]]], shape=(1, 2, 1), dtype=float32)
state [[ 0.17242002]
 [-7.988312  ]]
input [6828.3096]
input_C

state [[ 0.17474937]
 [-7.9849854 ]]
input [6882.5264]
input_CA0 [0.5]
3943 [[[ 0.15764642]
  [-7.978241  ]]]
tf.Tensor(
[[[ 0.15764642]
  [-7.978241  ]]], shape=(1, 2, 1), dtype=float32)
state [[ 0.15764642]
 [-7.978241  ]]
input [5768.5566]
input_CA0 [7.5]
3944 [[[ 0.17577076]
  [-7.983429  ]]]
tf.Tensor(
[[[ 0.17577076]
  [-7.983429  ]]], shape=(1, 2, 1), dtype=float32)
state [[ 0.17577076]
 [-7.983429  ]]
input [6882.4277]
input_CA0 [0.5]
3945 [[[ 0.1586535]
  [-7.9762573]]]
tf.Tensor(
[[[ 0.1586535]
  [-7.9762573]]], shape=(1, 2, 1), dtype=float32)
state [[ 0.1586535]
 [-7.9762573]]
input [5855.676]
input_CA0 [7.5]
3946 [[[ 0.17676353]
  [-7.9806213 ]]]
tf.Tensor(
[[[ 0.17676353]
  [-7.9806213 ]]], shape=(1, 2, 1), dtype=float32)
state [[ 0.17676353]
 [-7.9806213 ]]
input [6857.2773]
input_CA0 [0.5]
3947 [[[ 0.15963197]
  [-7.9730835 ]]]
tf.Tensor(
[[[ 0.15963197]
  [-7.9730835 ]]], shape=(1, 2, 1), dtype=float32)
state [[ 0.15963197]
 [-7.9730835 ]]
input [5938.117]
input_CA0 [7.

state [[ 0.18002915]
 [-7.9687805 ]]
input [6509.553]
input_CA0 [0.5]
3988 [[[ 0.16284943]
  [-7.9612427 ]]]
tf.Tensor(
[[[ 0.16284943]
  [-7.9612427 ]]], shape=(1, 2, 1), dtype=float32)
state [[ 0.16284943]
 [-7.9612427 ]]
input [6192.614]
input_CA0 [7.5]
3989 [[[ 0.18089819]
  [-7.9621887 ]]]
tf.Tensor(
[[[ 0.18089819]
  [-7.9621887 ]]], shape=(1, 2, 1), dtype=float32)
state [[ 0.18089819]
 [-7.9621887 ]]
input [6261.2476]
input_CA0 [0.5]
3990 [[[ 0.1637044]
  [-7.955261 ]]]
tf.Tensor(
[[[ 0.1637044]
  [-7.955261 ]]], shape=(1, 2, 1), dtype=float32)
state [[ 0.1637044]
 [-7.955261 ]]
input [6252.641]
input_CA0 [7.5]
3991 [[[ 0.18173957]
  [-7.955536  ]]]
tf.Tensor(
[[[ 0.18173957]
  [-7.955536  ]]], shape=(1, 2, 1), dtype=float32)
state [[ 0.18173957]
 [-7.955536  ]]
input [5908.4624]
input_CA0 [0.5]
3992 [[[ 0.16453218]
  [-7.949707  ]]]
tf.Tensor(
[[[ 0.16453218]
  [-7.949707  ]]], shape=(1, 2, 1), dtype=float32)
state [[ 0.16453218]
 [-7.949707  ]]
input [6307.813]
input_CA0 [7.5]

In [28]:
###left up. outside the ss
np.savetxt("trajectory_FCU1_new.txt",    np.array(update_states_list).reshape(-1,2), fmt="%f",  delimiter=" ")

In [29]:
###get trajectory data for ploting using LSNN to get sontag law, two sontag laws
update_states = [[-1.48,50]] ###-1.48,50

update_states_list = list()
#update_states_list.append(update_states)


for k in range(4000):
    update_states = tf.convert_to_tensor(update_states, dtype = tf.float32) ###convert the state to tensor
    print(update_states)
    Sontag_value = tf.reshape(model.dVsontag_value(update_states),(1))  ### get the sontag law
    Sontag_value_CA0 = tf.reshape(model.dVsontag_value_CA0(update_states),(1))  ### get the sontag law
    input_vector = list() ###generate the empty list
   
    state = update_states[0].numpy()
    print("state", state)
    inputs = Sontag_value.numpy()
    print('input',inputs)
    inputs_CA0 = Sontag_value_CA0.numpy() + 4
    print('input_CA0',inputs_CA0)
    collected_data = CSTR_simulation_update(state[0], state[1], inputs_CA0, inputs) ### C_A, T, dC, dT, note C_A and T are deviation
        #print('collected_date',collected_data)

    input_vector.append(collected_data)  ###convert the collected data to list

    input_vector = np.array(input_vector) ###convert the list to numpy array
    update_states = input_vector[-4:,:2]  ##3get the update states
    print(k, update_states)
    update_states_list.append(update_states[0])
print(update_states)

tf.Tensor([[-1.48 50.  ]], shape=(1, 2), dtype=float32)
state [-1.48 50.  ]
input [0.]
input_CA0 [7.5]
0 [[[-1.4479631]
  [49.39499  ]]]
tf.Tensor(
[[[-1.4479631]
  [49.39499  ]]], shape=(1, 2, 1), dtype=float32)
state [[-1.4479631]
 [49.39499  ]]
input [0.]
input_CA0 [7.5]
1 [[[-1.4164624]
  [48.811707 ]]]
tf.Tensor(
[[[-1.4164624]
  [48.811707 ]]], shape=(1, 2, 1), dtype=float32)
state [[-1.4164624]
 [48.811707 ]]
input [0.]
input_CA0 [7.5]
2 [[[-1.3855035]
  [48.25049  ]]]
tf.Tensor(
[[[-1.3855035]
  [48.25049  ]]], shape=(1, 2, 1), dtype=float32)
state [[-1.3855035]
 [48.25049  ]]
input [0.]
input_CA0 [7.5]
3 [[[-1.3550904]
  [47.711548 ]]]
tf.Tensor(
[[[-1.3550904]
  [47.711548 ]]], shape=(1, 2, 1), dtype=float32)
state [[-1.3550904]
 [47.711548 ]]
input [0.]
input_CA0 [7.5]
4 [[[-1.3252261]
  [47.195038 ]]]
tf.Tensor(
[[[-1.3252261]
  [47.195038 ]]], shape=(1, 2, 1), dtype=float32)
state [[-1.3252261]
 [47.195038 ]]
input [0.]
input_CA0 [7.5]
5 [[[-1.2959123]
  [46.70108  ]]]
tf.

state [[-0.81893694]
 [38.978607  ]]
input [-0.]
input_CA0 [7.5]
65 [[[-0.8000207]
  [38.917328 ]]]
tf.Tensor(
[[[-0.8000207]
  [38.917328 ]]], shape=(1, 2, 1), dtype=float32)
state [[-0.8000207]
 [38.917328 ]]
input [-0.]
input_CA0 [0.5]
66 [[[-0.81660986]
  [38.87683   ]]]
tf.Tensor(
[[[-0.81660986]
  [38.87683   ]]], shape=(1, 2, 1), dtype=float32)
state [[-0.81660986]
 [38.87683   ]]
input [-0.]
input_CA0 [7.5]
67 [[[-0.7977178]
  [38.81668  ]]]
tf.Tensor(
[[[-0.7977178]
  [38.81668  ]]], shape=(1, 2, 1), dtype=float32)
state [[-0.7977178]
 [38.81668  ]]
input [-0.]
input_CA0 [0.5]
68 [[[-0.81433034]
  [38.777252  ]]]
tf.Tensor(
[[[-0.81433034]
  [38.777252  ]]], shape=(1, 2, 1), dtype=float32)
state [[-0.81433034]
 [38.777252  ]]
input [-0.]
input_CA0 [7.5]
69 [[[-0.7954618]
  [38.71823  ]]]
tf.Tensor(
[[[-0.7954618]
  [38.71823  ]]], shape=(1, 2, 1), dtype=float32)
state [[-0.7954618]
 [38.71823  ]]
input [-0.]
input_CA0 [0.5]
70 [[[-0.8120971]
  [38.67987  ]]]
tf.Tensor(
[[[-0.8

state [[-0.7440642]
 [36.526886 ]]
input [-0.]
input_CA0 [0.5]
132 [[[-0.76121175]
  [36.512207  ]]]
tf.Tensor(
[[[-0.76121175]
  [36.512207  ]]], shape=(1, 2, 1), dtype=float32)
state [[-0.76121175]
 [36.512207  ]]
input [-0.]
input_CA0 [7.5]
133 [[[-0.74288297]
  [36.47815   ]]]
tf.Tensor(
[[[-0.74288297]
  [36.47815   ]]], shape=(1, 2, 1), dtype=float32)
state [[-0.74288297]
 [36.47815   ]]
input [-0.]
input_CA0 [0.5]
134 [[[-0.7600423]
  [36.46399  ]]]
tf.Tensor(
[[[-0.7600423]
  [36.46399  ]]], shape=(1, 2, 1), dtype=float32)
state [[-0.7600423]
 [36.46399  ]]
input [-0.]
input_CA0 [7.5]
135 [[[-0.74172544]
  [36.43048   ]]]
tf.Tensor(
[[[-0.74172544]
  [36.43048   ]]], shape=(1, 2, 1), dtype=float32)
state [[-0.74172544]
 [36.43048   ]]
input [-0.]
input_CA0 [0.5]
136 [[[-0.75889647]
  [36.41687   ]]]
tf.Tensor(
[[[-0.75889647]
  [36.41687   ]]], shape=(1, 2, 1), dtype=float32)
state [[-0.75889647]
 [36.41687   ]]
input [-0.]
input_CA0 [7.5]
137 [[[-0.7405913]
  [36.38388  ]]]
tf

state [[-0.73549795]
 [35.243347  ]]
input [-0.]
input_CA0 [7.5]
197 [[[-0.7173375]
  [35.21762  ]]]
tf.Tensor(
[[[-0.7173375]
  [35.21762  ]]], shape=(1, 2, 1), dtype=float32)
state [[-0.7173375]
 [35.21762  ]]
input [-0.]
input_CA0 [0.5]
198 [[[-0.7346566]
  [35.211365 ]]]
tf.Tensor(
[[[-0.7346566]
  [35.211365 ]]], shape=(1, 2, 1), dtype=float32)
state [[-0.7346566]
 [35.211365 ]]
input [-0.]
input_CA0 [7.5]
199 [[[-0.7165054]
  [35.186035 ]]]
tf.Tensor(
[[[-0.7165054]
  [35.186035 ]]], shape=(1, 2, 1), dtype=float32)
state [[-0.7165054]
 [35.186035 ]]
input [-0.]
input_CA0 [0.5]
200 [[[-0.73383343]
  [35.180176  ]]]
tf.Tensor(
[[[-0.73383343]
  [35.180176  ]]], shape=(1, 2, 1), dtype=float32)
state [[-0.73383343]
 [35.180176  ]]
input [-0.]
input_CA0 [7.5]
201 [[[-0.7156913]
  [35.155243 ]]]
tf.Tensor(
[[[-0.7156913]
  [35.155243 ]]], shape=(1, 2, 1), dtype=float32)
state [[-0.7156913]
 [35.155243 ]]
input [-0.]
input_CA0 [0.5]
202 [[[-0.7330283]
  [35.14978  ]]]
tf.Tensor(
[[[-0.7

state [[-0.6975877]
 [34.40915  ]]
input [-1680.7993]
input_CA0 [0.5]
262 [[[-0.71509194]
  [34.40396   ]]]
tf.Tensor(
[[[-0.71509194]
  [34.40396   ]]], shape=(1, 2, 1), dtype=float32)
state [[-0.71509194]
 [34.40396   ]]
input [-0.]
input_CA0 [7.5]
263 [[[-0.69712496]
  [34.386963  ]]]
tf.Tensor(
[[[-0.69712496]
  [34.386963  ]]], shape=(1, 2, 1), dtype=float32)
state [[-0.69712496]
 [34.386963  ]]
input [-1716.937]
input_CA0 [0.5]
264 [[[-0.71463203]
  [34.381744  ]]]
tf.Tensor(
[[[-0.71463203]
  [34.381744  ]]], shape=(1, 2, 1), dtype=float32)
state [[-0.71463203]
 [34.381744  ]]
input [-0.]
input_CA0 [7.5]
265 [[[-0.6966679]
  [34.3649   ]]]
tf.Tensor(
[[[-0.6966679]
  [34.3649   ]]], shape=(1, 2, 1), dtype=float32)
state [[-0.6966679]
 [34.3649   ]]
input [-1751.7162]
input_CA0 [0.5]
266 [[[-0.7141776]
  [34.35968  ]]]
tf.Tensor(
[[[-0.7141776]
  [34.35968  ]]], shape=(1, 2, 1), dtype=float32)
state [[-0.7141776]
 [34.35968  ]]
input [-0.]
input_CA0 [7.5]
267 [[[-0.69621634]
  [3

...

state [[-0.05236769]
 [ 2.5374756 ]]
input [-4184.8916]
input_CA0 [0.5]
3754 [[[-0.07000875]
  [ 2.527008  ]]]
tf.Tensor(
[[[-0.07000875]
  [ 2.527008  ]]], shape=(1, 2, 1), dtype=float32)
state [[-0.07000875]
 [ 2.527008  ]]
input [0.]
input_CA0 [7.5]
3755 [[[-0.05236042]
  [ 2.5246887 ]]]
tf.Tensor(
[[[-0.05236042]
  [ 2.5246887 ]]], shape=(1, 2, 1), dtype=float32)
state [[-0.05236042]
 [ 2.5246887 ]]
input [-4253.938]
input_CA0 [0.5]
3756 [[[-0.0699966]
  [ 2.513733 ]]]
tf.Tensor(
[[[-0.0699966]
  [ 2.513733 ]]], shape=(1, 2, 1), dtype=float32)
state [[-0.0699966]
 [ 2.513733 ]]
input [0.]
input_CA0 [7.5]
3757 [[[-0.05234337]
  [ 2.5112305 ]]]
tf.Tensor(
[[[-0.05234337]
  [ 2.5112305 ]]], shape=(1, 2, 1), dtype=float32)
state [[-0.05234337]
 [ 2.5112305 ]]
input [-4328.747]
input_CA0 [7.5]
3758 [[[-0.03497458]
  [ 2.4997864 ]]]
tf.Tensor(
[[[-0.03497458]
  [ 2.4997864 ]]], shape=(1, 2, 1), dtype=float32)
state [[-0.03497458]
 [ 2.4997864 ]]
input [-1152.2422]
input_CA0 [0.5]
3759 [[

state [[-0.05928528]
 [ 2.2396545 ]]
input [0.]
input_CA0 [7.5]
3798 [[[-0.04169905]
  [ 2.2391968 ]]]
tf.Tensor(
[[[-0.04169905]
  [ 2.2391968 ]]], shape=(1, 2, 1), dtype=float32)
state [[-0.04169905]
 [ 2.2391968 ]]
input [-2655.3232]
input_CA0 [0.5]
3799 [[[-0.05939603]
  [ 2.236969  ]]]
tf.Tensor(
[[[-0.05939603]
  [ 2.236969  ]]], shape=(1, 2, 1), dtype=float32)
state [[-0.05939603]
 [ 2.236969  ]]
input [0.]
input_CA0 [7.5]
3800 [[[-0.04180694]
  [ 2.2364197 ]]]
tf.Tensor(
[[[-0.04180694]
  [ 2.2364197 ]]], shape=(1, 2, 1), dtype=float32)
state [[-0.04180694]
 [ 2.2364197 ]]
input [-2685.3489]
input_CA0 [0.5]
3801 [[[-0.05950105]
  [ 2.2339783 ]]]
tf.Tensor(
[[[-0.05950105]
  [ 2.2339783 ]]], shape=(1, 2, 1), dtype=float32)
state [[-0.05950105]
 [ 2.2339783 ]]
input [0.]
input_CA0 [7.5]
3802 [[[-0.0419091]
  [ 2.2333374]]]
tf.Tensor(
[[[-0.0419091]
  [ 2.2333374]]], shape=(1, 2, 1), dtype=float32)
state [[-0.0419091]
 [ 2.2333374]]
input [-2715.518]
input_CA0 [0.5]
3803 [[[-0.059

state [[-0.05782735]
 [ 1.9633179 ]]
input [0.]
input_CA0 [7.5]
3864 [[[-0.04015839]
  [ 1.9597778 ]]]
tf.Tensor(
[[[-0.04015839]
  [ 1.9597778 ]]], shape=(1, 2, 1), dtype=float32)
state [[-0.04015839]
 [ 1.9597778 ]]
input [-3425.5994]
input_CA0 [0.5]
3865 [[[-0.05777097]
  [ 1.9510193 ]]]
tf.Tensor(
[[[-0.05777097]
  [ 1.9510193 ]]], shape=(1, 2, 1), dtype=float32)
state [[-0.05777097]
 [ 1.9510193 ]]
input [0.]
input_CA0 [7.5]
3866 [[[-0.04009831]
  [ 1.9473267 ]]]
tf.Tensor(
[[[-0.04009831]
  [ 1.9473267 ]]], shape=(1, 2, 1), dtype=float32)
state [[-0.04009831]
 [ 1.9473267 ]]
input [-3491.9155]
input_CA0 [0.5]
3867 [[[-0.05770707]
  [ 1.9381409 ]]]
tf.Tensor(
[[[-0.05770707]
  [ 1.9381409 ]]], shape=(1, 2, 1), dtype=float32)
state [[-0.05770707]
 [ 1.9381409 ]]
input [0.]
input_CA0 [7.5]
3868 [[[-0.04003048]
  [ 1.9342957 ]]]
tf.Tensor(
[[[-0.04003048]
  [ 1.9342957 ]]], shape=(1, 2, 1), dtype=float32)
state [[-0.04003048]
 [ 1.9342957 ]]
input [-3564.648]
input_CA0 [0.5]
3869 [[[

state [[-0.04763281]
 [ 1.8569641 ]]
input [173.61938]
input_CA0 [7.5]
3929 [[[-0.03008592]
  [ 1.8582458 ]]]
tf.Tensor(
[[[-0.03008592]
  [ 1.8582458 ]]], shape=(1, 2, 1), dtype=float32)
state [[-0.03008592]
 [ 1.8582458 ]]
input [-1345.9509]
input_CA0 [0.5]
3930 [[[-0.04782081]
  [ 1.8625793 ]]]
tf.Tensor(
[[[-0.04782081]
  [ 1.8625793 ]]], shape=(1, 2, 1), dtype=float32)
state [[-0.04782081]
 [ 1.8625793 ]]
input [119.0428]
input_CA0 [7.5]
3931 [[[-0.03027308]
  [ 1.8635864 ]]]
tf.Tensor(
[[[-0.03027308]
  [ 1.8635864 ]]], shape=(1, 2, 1), dtype=float32)
state [[-0.03027308]
 [ 1.8635864 ]]
input [-1368.0906]
input_CA0 [0.5]
3932 [[[-0.04800701]
  [ 1.8677979 ]]]
tf.Tensor(
[[[-0.04800701]
  [ 1.8677979 ]]], shape=(1, 2, 1), dtype=float32)
state [[-0.04800701]
 [ 1.8677979 ]]
input [59.78551]
input_CA0 [7.5]
3933 [[[-0.03045833]
  [ 1.8685303 ]]]
tf.Tensor(
[[[-0.03045833]
  [ 1.8685303 ]]], shape=(1, 2, 1), dtype=float32)
state [[-0.03045833]
 [ 1.8685303 ]]
input [-1390.6741]
inpu

state [[-0.05236781]
 [ 1.920105  ]]
input [0.]
input_CA0 [7.5]
3995 [[[-0.03476954]
  [ 1.9189148 ]]]
tf.Tensor(
[[[-0.03476954]
  [ 1.9189148 ]]], shape=(1, 2, 1), dtype=float32)
state [[-0.03476954]
 [ 1.9189148 ]]
input [-2092.436]
input_CA0 [0.5]
3996 [[[-0.0524528]
  [ 1.918335 ]]]
tf.Tensor(
[[[-0.0524528]
  [ 1.918335 ]]], shape=(1, 2, 1), dtype=float32)
state [[-0.0524528]
 [ 1.918335 ]]
input [0.]
input_CA0 [7.5]
3997 [[[-0.0348525]
  [ 1.9170837]]]
tf.Tensor(
[[[-0.0348525]
  [ 1.9170837]]], shape=(1, 2, 1), dtype=float32)
state [[-0.0348525]
 [ 1.9170837]]
input [-2115.1812]
input_CA0 [0.5]
3998 [[[-0.05253375]
  [ 1.9163208 ]]]
tf.Tensor(
[[[-0.05253375]
  [ 1.9163208 ]]], shape=(1, 2, 1), dtype=float32)
state [[-0.05253375]
 [ 1.9163208 ]]
input [0.]
input_CA0 [7.5]
3999 [[[-0.03493142]
  [ 1.9150085 ]]]
[[[-0.03493142]
  [ 1.9150085 ]]]


In [30]:
###left up inside the ss 
np.savetxt("trajectory_FCU2_new.txt",    np.array(update_states_list).reshape(-1,2), fmt="%f",  delimiter=" ")

In [31]:
###get trajectory data for ploting using LSNN to get sontag law, two sontag laws
update_states = [[-1.3,	65]]

update_states_list = list()
#update_states_list.append(update_states)


for k in range(4000):
    update_states = tf.convert_to_tensor(update_states, dtype = tf.float32) ###convert the state to tensor
    print(update_states)
    Sontag_value = tf.reshape(model.dVsontag_value(update_states),(1))  ### get the sontag law
    Sontag_value_CA0 = tf.reshape(model.dVsontag_value_CA0(update_states),(1))  ### get the sontag law
    input_vector = list() ###generate the empty list
   
    state = update_states[0].numpy()
    print("state", state)
    inputs = Sontag_value.numpy()
    print('input',inputs)
    inputs_CA0 = Sontag_value_CA0.numpy() + 4
    print('input_CA0',inputs_CA0)
    collected_data = CSTR_simulation_update(state[0], state[1], inputs_CA0, inputs) ### C_A, T, dC, dT, note C_A and T are deviation
        #print('collected_date',collected_data)

    input_vector.append(collected_data)  ###convert the collected data to list

    input_vector = np.array(input_vector) ###convert the list to numpy array
    update_states = input_vector[-4:,:2]  ##3get the update states
    print(k, update_states)
    update_states_list.append(update_states[0])
print(update_states)

tf.Tensor([[-1.3 65. ]], shape=(1, 2), dtype=float32)
state [-1.3 65. ]
input [-0.]
input_CA0 [0.5]
0 [[[-1.309879]
  [64.61948 ]]]
tf.Tensor(
[[[-1.309879]
  [64.61948 ]]], shape=(1, 2, 1), dtype=float32)
state [[-1.309879]
 [64.61948 ]]
input [-0.]
input_CA0 [0.5]
1 [[[-1.3193407]
  [64.222534 ]]]
tf.Tensor(
[[[-1.3193407]
  [64.222534 ]]], shape=(1, 2, 1), dtype=float32)
state [[-1.3193407]
 [64.222534 ]]
input [-0.]
input_CA0 [0.5]
2 [[[-1.3284051]
  [63.81015  ]]]
tf.Tensor(
[[[-1.3284051]
  [63.81015  ]]], shape=(1, 2, 1), dtype=float32)
state [[-1.3284051]
 [63.81015  ]]
input [-0.]
input_CA0 [7.5]
3 [[[-1.3020915]
  [63.38327  ]]]
tf.Tensor(
[[[-1.3020915]
  [63.38327  ]]], shape=(1, 2, 1), dtype=float32)
state [[-1.3020915]
 [63.38327  ]]
input [-0.]
input_CA0 [0.5]
4 [[[-1.3115045]
  [62.98816  ]]]
tf.Tensor(
[[[-1.3115045]
  [62.98816  ]]], shape=(1, 2, 1), dtype=float32)
state [[-1.3115045]
 [62.98816  ]]
input [-0.]
input_CA0 [7.5]
5 [[[-1.2855282]
  [62.577972 ]]]
tf.Tens

state [[-1.018435]
 [48.868652]]
input [-0.]
input_CA0 [7.5]
61 [[[-0.9974211]
  [48.703156 ]]]
tf.Tensor(
[[[-0.9974211]
  [48.703156 ]]], shape=(1, 2, 1), dtype=float32)
state [[-0.9974211]
 [48.703156 ]]
input [-0.]
input_CA0 [0.5]
62 [[[-1.0119915]
  [48.562347 ]]]
tf.Tensor(
[[[-1.0119915]
  [48.562347 ]]], shape=(1, 2, 1), dtype=float32)
state [[-1.0119915]
 [48.562347 ]]
input [-0.]
input_CA0 [7.5]
63 [[[-0.99106574]
  [48.401184  ]]]
tf.Tensor(
[[[-0.99106574]
  [48.401184  ]]], shape=(1, 2, 1), dtype=float32)
state [[-0.99106574]
 [48.401184  ]]
input [-0.]
input_CA0 [0.5]
64 [[[-1.0057216]
  [48.264557 ]]]
tf.Tensor(
[[[-1.0057216]
  [48.264557 ]]], shape=(1, 2, 1), dtype=float32)
state [[-1.0057216]
 [48.264557 ]]
input [-0.]
input_CA0 [7.5]
65 [[[-0.9848807]
  [48.107544 ]]]
tf.Tensor(
[[[-0.9848807]
  [48.107544 ]]], shape=(1, 2, 1), dtype=float32)
state [[-0.9848807]
 [48.107544 ]]
input [-0.]
input_CA0 [0.5]
66 [[[-0.9996188]
  [47.974945 ]]]
tf.Tensor(
[[[-0.9996188]
  

state [[-0.87272525]
 [41.96988   ]]
input [-0.]
input_CA0 [7.5]
127 [[[-0.8534684]
  [41.890076 ]]]
tf.Tensor(
[[[-0.8534684]
  [41.890076 ]]], shape=(1, 2, 1), dtype=float32)
state [[-0.8534684]
 [41.890076 ]]
input [-0.]
input_CA0 [0.5]
128 [[[-0.8697392]
  [41.832153 ]]]
tf.Tensor(
[[[-0.8697392]
  [41.832153 ]]], shape=(1, 2, 1), dtype=float32)
state [[-0.8697392]
 [41.832153 ]]
input [-0.]
input_CA0 [7.5]
129 [[[-0.8505144]
  [41.753906 ]]]
tf.Tensor(
[[[-0.8505144]
  [41.753906 ]]], shape=(1, 2, 1), dtype=float32)
state [[-0.8505144]
 [41.753906 ]]
input [-0.]
input_CA0 [0.5]
130 [[[-0.8668163]
  [41.69748  ]]]
tf.Tensor(
[[[-0.8668163]
  [41.69748  ]]], shape=(1, 2, 1), dtype=float32)
state [[-0.8668163]
 [41.69748  ]]
input [-0.]
input_CA0 [7.5]
131 [[[-0.84762275]
  [41.620728  ]]]
tf.Tensor(
[[[-0.84762275]
  [41.620728  ]]], shape=(1, 2, 1), dtype=float32)
state [[-0.84762275]
 [41.620728  ]]
input [-0.]
input_CA0 [0.5]
132 [[[-0.8639548]
  [41.565735 ]]]
tf.Tensor(
[[[-0.8

state [[-0.7839649]
 [38.509857 ]]
input [-0.]
input_CA0 [0.5]
192 [[[-0.8008374]
  [38.481506 ]]]
tf.Tensor(
[[[-0.8008374]
  [38.481506 ]]], shape=(1, 2, 1), dtype=float32)
state [[-0.8008374]
 [38.481506 ]]
input [-0.]
input_CA0 [7.5]
193 [[[-0.782225]
  [38.43335 ]]]
tf.Tensor(
[[[-0.782225]
  [38.43335 ]]], shape=(1, 2, 1), dtype=float32)
state [[-0.782225]
 [38.43335 ]]
input [-0.]
input_CA0 [0.5]
194 [[[-0.7991146]
  [38.405792 ]]]
tf.Tensor(
[[[-0.7991146]
  [38.405792 ]]], shape=(1, 2, 1), dtype=float32)
state [[-0.7991146]
 [38.405792 ]]
input [-0.]
input_CA0 [7.5]
195 [[[-0.78051925]
  [38.35843   ]]]
tf.Tensor(
[[[-0.78051925]
  [38.35843   ]]], shape=(1, 2, 1), dtype=float32)
state [[-0.78051925]
 [38.35843   ]]
input [-0.]
input_CA0 [0.5]
196 [[[-0.7974254]
  [38.331635 ]]]
tf.Tensor(
[[[-0.7974254]
  [38.331635 ]]], shape=(1, 2, 1), dtype=float32)
state [[-0.7974254]
 [38.331635 ]]
input [-0.]
input_CA0 [7.5]
197 [[[-0.77884686]
  [38.285065  ]]]
tf.Tensor(
[[[-0.7788468

input_CA0 [7.5]
257 [[[-0.74127233]
  [36.468445  ]]]
tf.Tensor(
[[[-0.74127233]
  [36.468445  ]]], shape=(1, 2, 1), dtype=float32)
state [[-0.74127233]
 [36.468445  ]]
input [-0.]
input_CA0 [0.5]
258 [[[-0.75847197]
  [36.455963  ]]]
tf.Tensor(
[[[-0.75847197]
  [36.455963  ]]], shape=(1, 2, 1), dtype=float32)
state [[-0.75847197]
 [36.455963  ]]
input [-0.]
input_CA0 [7.5]
259 [[[-0.74019456]
  [36.424072  ]]]
tf.Tensor(
[[[-0.74019456]
  [36.424072  ]]], shape=(1, 2, 1), dtype=float32)
state [[-0.74019456]
 [36.424072  ]]
input [-0.]
input_CA0 [0.5]
260 [[[-0.75740504]
  [36.41208   ]]]
tf.Tensor(
[[[-0.75740504]
  [36.41208   ]]], shape=(1, 2, 1), dtype=float32)
state [[-0.75740504]
 [36.41208   ]]
input [-0.]
input_CA0 [7.5]
261 [[[-0.7391385]
  [36.380676 ]]]
tf.Tensor(
[[[-0.7391385]
  [36.380676 ]]], shape=(1, 2, 1), dtype=float32)
state [[-0.7391385]
 [36.380676 ]]
input [-0.]
input_CA0 [0.5]
262 [[[-0.75635946]
  [36.36914   ]]]
tf.Tensor(
[[[-0.75635946]
  [36.36914   ]]], s

...

state [[-0.01547348]
 [ 1.0766296 ]]
input [-221.00148]
input_CA0 [0.5]
3748 [[[-0.03313661]
  [ 1.08255   ]]]
tf.Tensor(
[[[-0.03313661]
  [ 1.08255   ]]], shape=(1, 2, 1), dtype=float32)
state [[-0.03313661]
 [ 1.08255   ]]
input [0.]
input_CA0 [7.5]
3749 [[[-0.01552296]
  [ 1.0800171 ]]]
tf.Tensor(
[[[-0.01552296]
  [ 1.0800171 ]]], shape=(1, 2, 1), dtype=float32)
state [[-0.01552296]
 [ 1.0800171 ]]
input [-223.66003]
input_CA0 [0.5]
3750 [[[-0.03318655]
  [ 1.0859375 ]]]
tf.Tensor(
[[[-0.03318655]
  [ 1.0859375 ]]], shape=(1, 2, 1), dtype=float32)
state [[-0.03318655]
 [ 1.0859375 ]]
input [0.]
input_CA0 [7.5]
3751 [[[-0.01557338]
  [ 1.0834045 ]]]
tf.Tensor(
[[[-0.01557338]
  [ 1.0834045 ]]], shape=(1, 2, 1), dtype=float32)
state [[-0.01557338]
 [ 1.0834045 ]]
input [-226.53365]
input_CA0 [0.5]
3752 [[[-0.03323746]
  [ 1.089325  ]]]
tf.Tensor(
[[[-0.03323746]
  [ 1.089325  ]]], shape=(1, 2, 1), dtype=float32)
state [[-0.03323746]
 [ 1.089325  ]]
input [0.]
input_CA0 [7.5]
3753 [[

state [[-0.01684999]
 [ 1.1602783 ]]
input [-315.74127]
input_CA0 [0.5]
3794 [[[-0.03452373]
  [ 1.1662292 ]]]
tf.Tensor(
[[[-0.03452373]
  [ 1.1662292 ]]], shape=(1, 2, 1), dtype=float32)
state [[-0.03452373]
 [ 1.1662292 ]]
input [0.]
input_CA0 [7.5]
3795 [[[-0.01692009]
  [ 1.1641235 ]]]
tf.Tensor(
[[[-0.01692009]
  [ 1.1641235 ]]], shape=(1, 2, 1), dtype=float32)
state [[-0.01692009]
 [ 1.1641235 ]]
input [-321.32224]
input_CA0 [0.5]
3796 [[[-0.03459418]
  [ 1.1700745 ]]]
tf.Tensor(
[[[-0.03459418]
  [ 1.1700745 ]]], shape=(1, 2, 1), dtype=float32)
state [[-0.03459418]
 [ 1.1700745 ]]
input [0.]
input_CA0 [7.5]
3797 [[[-0.0169909]
  [ 1.1679688]]]
tf.Tensor(
[[[-0.0169909]
  [ 1.1679688]]], shape=(1, 2, 1), dtype=float32)
state [[-0.0169909]
 [ 1.1679688]]
input [-327.02606]
input_CA0 [0.5]
3798 [[[-0.03466535]
  [ 1.1739197 ]]]
tf.Tensor(
[[[-0.03466535]
  [ 1.1739197 ]]], shape=(1, 2, 1), dtype=float32)
state [[-0.03466535]
 [ 1.1739197 ]]
input [0.]
input_CA0 [7.5]
3799 [[[-0.01

state [[-0.01945114]
 [ 1.2860107 ]]
input [-552.61584]
input_CA0 [0.5]
3860 [[[-0.0371325]
  [ 1.2913513]]]
tf.Tensor(
[[[-0.0371325]
  [ 1.2913513]]], shape=(1, 2, 1), dtype=float32)
state [[-0.0371325]
 [ 1.2913513]]
input [0.]
input_CA0 [7.5]
3861 [[[-0.01953554]
  [ 1.2895813 ]]]
tf.Tensor(
[[[-0.01953554]
  [ 1.2895813 ]]], shape=(1, 2, 1), dtype=float32)
state [[-0.01953554]
 [ 1.2895813 ]]
input [-561.2171]
input_CA0 [0.5]
3862 [[[-0.0372169]
  [ 1.2948914]]]
tf.Tensor(
[[[-0.0372169]
  [ 1.2948914]]], shape=(1, 2, 1), dtype=float32)
state [[-0.0372169]
 [ 1.2948914]]
input [0.]
input_CA0 [7.5]
3863 [[[-0.01961994]
  [ 1.2931213 ]]]
tf.Tensor(
[[[-0.01961994]
  [ 1.2931213 ]]], shape=(1, 2, 1), dtype=float32)
state [[-0.01961994]
 [ 1.2931213 ]]
input [-569.8779]
input_CA0 [0.5]
3864 [[[-0.0373013]
  [ 1.2983704]]]
tf.Tensor(
[[[-0.0373013]
  [ 1.2983704]]], shape=(1, 2, 1), dtype=float32)
state [[-0.0373013]
 [ 1.2983704]]
input [0.]
input_CA0 [7.5]
3865 [[[-0.01970434]
  [ 1.

state [[-0.03896379]
 [ 1.3609009 ]]
input [0.]
input_CA0 [7.5]
3905 [[[-0.02136445]
  [ 1.3591309 ]]]
tf.Tensor(
[[[-0.02136445]
  [ 1.3591309 ]]], shape=(1, 2, 1), dtype=float32)
state [[-0.02136445]
 [ 1.3591309 ]]
input [-763.24915]
input_CA0 [0.5]
3906 [[[-0.03904378]
  [ 1.3635559 ]]]
tf.Tensor(
[[[-0.03904378]
  [ 1.3635559 ]]], shape=(1, 2, 1), dtype=float32)
state [[-0.03904378]
 [ 1.3635559 ]]
input [0.]
input_CA0 [7.5]
3907 [[[-0.0214442]
  [ 1.3617859]]]
tf.Tensor(
[[[-0.0214442]
  [ 1.3617859]]], shape=(1, 2, 1), dtype=float32)
state [[-0.0214442]
 [ 1.3617859]]
input [-772.8724]
input_CA0 [0.5]
3908 [[[-0.0391233]
  [ 1.3661804]]]
tf.Tensor(
[[[-0.0391233]
  [ 1.3661804]]], shape=(1, 2, 1), dtype=float32)
state [[-0.0391233]
 [ 1.3661804]]
input [0.]
input_CA0 [7.5]
3909 [[[-0.02152336]
  [ 1.3644104 ]]]
tf.Tensor(
[[[-0.02152336]
  [ 1.3644104 ]]], shape=(1, 2, 1), dtype=float32)
state [[-0.02152336]
 [ 1.3644104 ]]
input [-782.4537]
input_CA0 [0.5]
3910 [[[-0.03920221]


state [[-0.02359331]
 [ 1.4128418 ]]
input [-1084.8021]
input_CA0 [0.5]
3972 [[[-0.0412581]
  [ 1.4154358]]]
tf.Tensor(
[[[-0.0412581]
  [ 1.4154358]]], shape=(1, 2, 1), dtype=float32)
state [[-0.0412581]
 [ 1.4154358]]
input [0.]
input_CA0 [7.5]
3973 [[[-0.02364326]
  [ 1.4131775 ]]]
tf.Tensor(
[[[-0.02364326]
  [ 1.4131775 ]]], shape=(1, 2, 1), dtype=float32)
state [[-0.02364326]
 [ 1.4131775 ]]
input [-1094.4574]
input_CA0 [0.5]
3974 [[[-0.04130733]
  [ 1.4157104 ]]]
tf.Tensor(
[[[-0.04130733]
  [ 1.4157104 ]]], shape=(1, 2, 1), dtype=float32)
state [[-0.04130733]
 [ 1.4157104 ]]
input [0.]
input_CA0 [7.5]
3975 [[[-0.02369177]
  [ 1.4134521 ]]]
tf.Tensor(
[[[-0.02369177]
  [ 1.4134521 ]]], shape=(1, 2, 1), dtype=float32)
state [[-0.02369177]
 [ 1.4134521 ]]
input [-1103.9764]
input_CA0 [0.5]
3976 [[[-0.04135513]
  [ 1.4159241 ]]]
tf.Tensor(
[[[-0.04135513]
  [ 1.4159241 ]]], shape=(1, 2, 1), dtype=float32)
state [[-0.04135513]
 [ 1.4159241 ]]
input [0.]
input_CA0 [7.5]
3977 [[[-0.02

In [32]:
np.savetxt("trajectory_FCU3_new.txt",    np.array(update_states_list).reshape(-1,2), fmt="%f",  delimiter=" ")